### TO-DO

fix the model issue -> get nice models trained on rolling windows to represent time changes<br>
save all models - > load all models <br>
<br>
interpret each model for each bin: model1 - bin 1 to 9; model2 - bin 1 to 9, etc.<br>
PDP, ALE, permuation importance, correlation matrix<br>
decide which features to interpret in the nest step: <br>
shapley, LIME (change the feature indices and the number of samples)<br>
graph things: shapley - for each bin, graph results over time (9 graphs); <br>

In [1]:
import numpy as np
import pandas as pd

In [2]:
dtype_specification = {'SICCD': str}

In [17]:
df = pd.read_csv('less_messy_data_keyword_LESS.csv', dtype=dtype_specification)

In [4]:
df.columns

Index(['Unnamed: 0.1', 'Unnamed: 0', 'Date', 'permno', 'return', 'mom1m',
       'mom12m', 'chmom', 'indmom', 'mom36m', 'turn', 'mvel1', 'dolvol', 'ill',
       'zerotrade', 'baspread', 'retvol', 'idiovol', 'beta', 'betasq', 'ep',
       'sp', 'agr', 'nincr', 'return(t-1)', 'r(t+1)', 'SICCD', 'COMNAM'],
      dtype='object')

In [18]:
# df = df.drop(columns = ['COMNAM', 'Unnamed: 0.1', 'Unnamed: 0', 'r(t+1)' , 'return'])
df = df.drop(columns = ['COMNAM', 'Unnamed: 0.1', 'Unnamed: 0', 'return'])

In [19]:
df = df.dropna()

In [20]:
df

Date  permno     mom1m    mom12m     chmom    indmom    mom36m  \
365    2001-02-28   13610 -1.574474  0.371761  0.494096 -0.336094 -0.671895   
366    2001-02-28   13856 -0.955058  0.649673 -0.761935  0.007627 -0.390796   
367    2001-02-28   13901 -0.093663  2.181353  1.062388  2.002047 -0.847184   
368    2001-02-28   13928  0.146188  0.572134 -0.220966  2.002047 -0.384159   
369    2001-02-28   13936 -0.147475  1.592410  0.196068 -0.512919 -0.819860   
...           ...     ...       ...       ...       ...       ...       ...   
82850  2019-11-30   88841 -1.164215 -0.118785 -0.141530 -0.158082 -0.176577   
82851  2019-11-30   88853 -1.320755 -1.331099 -0.999018 -0.809971 -0.499509   
82852  2019-11-30   89279  0.396457 -0.882638  0.024604 -0.369627  0.196455   
82853  2019-11-30   89317  0.029003 -0.436975  0.033878 -0.569600  1.671328   
82854  2019-11-30   89790 -0.416172 -0.187693 -0.691035 -1.793787  0.297655   

           turn     mvel1    dolvol  ...   idiovol      beta    betasq  \
365   -0.346706 -0.249674  0.184594  ...  0.094682 -1.147764 -0.824350   
366   -0.534303  2.462294  1.587350  ... -0.367442 -1.584168 -0.903136   
367   -0.456468  3.941007  1.606840  ... -0.149938 -1.742606 -0.911117   
368   -0.448831  0.362108  1.108485  ... -0.525400 -1.545497 -0.899520   
369   -0.461310 -0.269049 -0.330978  ...  0.428061 -0.104307 -0.298094   
...         ...       ...       ...  ...       ...       ...       ...   
82850 -0.191830 -0.264013 -0.057238  ... -0.473570  0.105286 -0.134922   
82851  1.569748 -0.186750  0.979610  ... -0.168942  1.698117  1.733314   
82852 -0.806187 -0.277861 -1.100697  ... -0.627634  0.202993 -0.052285   
82853 -0.902458 -0.272401 -1.684172  ...  0.948616  0.613255  0.340296   
82854 -0.035903 -0.200907  0.488753  ...  1.449220  1.015619  0.796865   

             ep        sp       agr     nincr  return(t-1)    r(t+1)  SICCD  
365    0.109832 -0.005714  1.352752  3.271570    -1.577213 -0.175120   2810  
366    0.164941 -0.435813  1.039952  0.044234    -0.928233 -0.411877   2090  
367    0.435438 -0.135575  0.262103  0.851068    -0.033864 -0.092259   2110  
368    0.194226 -0.139399  0.122298  0.044234     0.129661  0.145672   2910  
369    0.300888  2.164993  0.340622  0.044234    -0.006530  0.123070   2310  
...         ...       ...       ...       ...          ...       ...    ...  
82850  0.153870 -0.097746 -0.248059 -0.762600    -1.124473  0.303352   6022  
82851  0.191346  1.109432  0.476213 -0.762600    -1.205177  0.563200   1629  
82852  0.146997 -0.516974  0.089618  0.044234     0.378648  0.391638   6020  
82853  0.984190 -0.371310  1.407156 -0.762600     0.035555  0.999422   6698  
82854 -0.138276 -0.592114 -1.143443 -0.762600    -0.349223 -0.061717   1311  

[82490 rows x 24 columns]

In [7]:
df.set_index('Date', inplace=True, drop = True)

### create bins

In [70]:
sorted(df['SICCD'].unique().tolist())

['0200',
 '1310',
 '1311',
 '1380',
 '1429',
 '1521',
 '1623',
 '1629',
 '2013',
 '2046',
 '2070',
 '2080',
 '2090',
 '2110',
 '2190',
 '2270',
 '2282',
 '2310',
 '2329',
 '2330',
 '2339',
 '2510',
 '2522',
 '2541',
 '2640',
 '2672',
 '2710',
 '2711',
 '2810',
 '2819',
 '2821',
 '2830',
 '2834',
 '2836',
 '2840',
 '2844',
 '2850',
 '2890',
 '2910',
 '2911',
 '2992',
 '3010',
 '3079',
 '3081',
 '3089',
 '3140',
 '3171',
 '3210',
 '3241',
 '3291',
 '3296',
 '3310',
 '3360',
 '3399',
 '3420',
 '3440',
 '3460',
 '3465',
 '3490',
 '3499',
 '3510',
 '3520',
 '3523',
 '3533',
 '3540',
 '3550',
 '3560',
 '3570',
 '3577',
 '3585',
 '3610',
 '3629',
 '3660',
 '3661',
 '3663',
 '3670',
 '3672',
 '3674',
 '3679',
 '3690',
 '3692',
 '3710',
 '3714',
 '3715',
 '3720',
 '3743',
 '3810',
 '3811',
 '3820',
 '3826',
 '3840',
 '3845',
 '3860',
 '3861',
 '3910',
 '3970',
 '4190',
 '4200',
 '4210',
 '4212',
 '4730',
 '4812',
 '4813',
 '4832',
 '4833',
 '4890',
 '4910',
 '4911',
 '4920',
 '4924',
 '4930',
 

In [8]:
bins_y = list()

In [9]:
bin0 = df[df['SICCD'].str.startswith('0')]
bins_y.append(bin0)

bin1 = df[df['SICCD'].str.startswith('1')]
bins_y.append(bin1)

bin2 = df[df['SICCD'].str.startswith('2')]
bins_y.append(bin2)

bin3 = df[df['SICCD'].str.startswith('3')]
bins_y.append(bin3)

bin4 = df[df['SICCD'].str.startswith('4')]
bins_y.append(bin4)

bin5 = df[df['SICCD'].str.startswith('5')]
bins_y.append(bin5)

bin6 = df[df['SICCD'].str.startswith('6')]
bins_y.append(bin6)

bin7 = df[df['SICCD'].str.startswith('7')]
bins_y.append(bin7)

bin8 = df[df['SICCD'].str.startswith('8')]
bins_y.append(bin8)


In [10]:
for itm in bins_y:
    itm.drop(columns=['SICCD', 'permno'], inplace=True)

C:\Users\LL\AppData\Local\Temp\ipykernel_1816\4253811862.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  itm.drop(columns=['SICCD', 'permno'], inplace=True)
C:\Users\LL\AppData\Local\Temp\ipykernel_1816\4253811862.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  itm.drop(columns=['SICCD', 'permno'], inplace=True)
C:\Users\LL\AppData\Local\Temp\ipykernel_1816\4253811862.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  itm.drop

In [11]:
pd.to_pickle(bins_y, 'bins_y.pkl')

### read pickle

In [64]:
bins = pd.read_pickle('dataframes.pkl')

In [68]:
# len of each bin
for item in bins:
    print(len(item))
    print('------')

227
------
2270
------
11350
------
23154
------
6129
------
9988
------
17706
------
6356
------
5675
------


In [65]:
print(bins[0].columns)
print(len(bins[0].columns))

Index(['mom1m', 'mom12m', 'chmom', 'indmom', 'mom36m', 'turn', 'mvel1',
       'dolvol', 'ill', 'zerotrade', 'baspread', 'retvol', 'idiovol', 'beta',
       'betasq', 'ep', 'sp', 'agr', 'nincr', 'return(t-1)'],
      dtype='object')
20


### load models

In [7]:
import pickle

In [25]:
import tensorflow as tf
import keras

@keras.saving.register_keras_serializable()
def r2_score_wo_demeaning_nn(y_true, y_pred):
    ss_res = tf.reduce_sum(tf.square(y_true - y_pred))
    ss_tot = tf.reduce_sum(tf.square(y_true - 0))
    r2 = 1 - (ss_res / ss_tot)
    return r2

In [26]:
with open('models_NN.pkl', 'rb') as f:
    models_NN = pickle.load(f)

In [16]:
# NN

from keras import layers
from keras import Sequential

In [49]:
# for i in range(len(bins)):
#     bins[i] = bins[i].values

In [69]:
type(bins[0])

pandas.core.frame.DataFrame

### interpreting
***
PDP<br>
ALE<br>
permulation feature importance<br>
correlation matrix<br>

In [62]:
import matplotlib.pyplot as plt

In [52]:
features = ['mom1m', 'mom12m', 'chmom', 'indmom', 'mom36m', 'turn', 'mvel1',
       'dolvol', 'ill', 'zerotrade', 'baspread', 'retvol', 'idiovol', 'beta',
       'betasq', 'ep', 'sp', 'agr', 'nincr', 'return(t-1)']

### interpreting - Shapley

In [63]:
from itertools import combinations
import math

**for model one**

In [73]:
# load model into obj model
model = models_NN[0]

In [74]:
M = 10  # the number of random samples to calculate marginal contribution from
n_features = len(bins[0].columns)
feature_idxs = [7, 10, 16]
sample_to_explain = list()
shapley_value_all = list()


for df in bins:  # for each bin
    samplex = df.sample(10)  # sample 10 rows
    sample_to_explain.append(samplex)  # append them to a list
    xarray = samplex.values   # convert them to array
    
    for i in range(10):
        x = xarray[i]  # set x as the instance of interest aka the sample of index i
        print("selected instance: ", x)  # print out the instance of interest
        shapley_values = []

        for i in range(3):   # for each feature of interest
            x_idx = [7, 10, 16]
            marg_contri_feature = []

            feature_of_interest = feature_idxs[i]  # select the feature we are examining
            print("Index of feature of interest: ", feature_of_interest)
            x_idx.remove(feature_of_interest)  # the rest of the features we are about to examine

            all_combinations = []  # all coalitions of features minus the feature of interest
            for r in range(1, len(x_idx) + 1):   # generate combinations of features
                combinations_of_length_r = list(combinations(x_idx, r))
                all_combinations.extend(combinations_of_length_r)

            for coalition in all_combinations:  # for each coalition
                coalition = list(coalition)
                print('the current coalition: ', coalition)
                weight = math.factorial(len(coalition)) * math.factorial(n_features - len(coalition)-1)/ math.factorial(n_features)
                print("weight of this coalition: ", weight)

                marg_contri_coalition = []  # marginal contributions of this coalition

                for _ in range(M):
                    z = df.sample(1).values[0]  # random select sample    

                    # construct two new instances
                    x_orig = np.array([x[i] if i in coalition + [feature_of_interest] else z[i] for i in range(n_features)])
                    x_rando = np.array([x[i] if i in coalition else z[i] for i in range(n_features)])             

                    # calculate marginal contribution
                    marginal_contribution = model.predict(x_orig.reshape(1, -1))[0][0] - model.predict(x_rando.reshape(1, -1))[0][0]
                    marg_contri_coalition.append(marginal_contribution)

                sigma_j = sum(marg_contri_coalition) / len(marg_contri_coalition)
                shapley_coalition = sigma_j*weight  # for one coaltion examined for feature of interest
                marg_contri_feature.append(shapley_coalition)

            shapley_j = sum(marg_contri_feature)  # shapley value of feature j
            shapley_values.append(shapley_j)

            print("feature of interest: ", feature_of_interest)
            print("shapley value of this feature: ", shapley_j)
            print('--------')
            print('--------')
        shapley_value_all.append(shapley_values)

selected instance:  [ 0.52844821 -0.06491676  0.22432639 -1.48321591 -0.1683957  -0.44007967
 -0.25036571 -0.10814072 -0.11014943 -0.18796559 -0.49483877 -0.45778258
 -0.38410519 -0.57370973 -0.59379269  0.28487916 -0.06520946  0.29087103
 -0.76259956  0.47160772]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 50ms/step
feature of interest:  7
shapley value of this feature:  -2.0015000621652085e-06
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coali

1/1 [==============================] - 0s 43ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 47ms/step
feature of interest:  10
shapley value of this feature:  -8.593876982292932e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 58ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 48ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 42ms/step
feature of interest:  16
shapley value of this feature:  -1.90476883660283e-05
--------
--------
selected instance:  [ 1.10033758  0.38071551 -0.89775586 -0.29953909  0.44350909  0.39100088
 -0.19994931  0.64111883 -0.11056053 -0.1879656  -0.35671446 -0.16204425
 -0.57964366 -0.63869514 -0.

1/1 [==============================] - 0s 41ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 49ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 41ms/step
feature of interest:  7
shapley value of this feature:  0.00012969930920401335
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 40ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 41ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 51ms/step
feature of interest:  10
shapley value of this feature:  2.1361569432835832e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
we

1/1 [==============================] - 0s 47ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 48ms/step
feature of interest:  16
shapley value of this feature:  -1.7417494523507813e-05
--------
--------
selected instance:  [-0.57470851 -0.11238504  0.77266512 -0.12469094 -0.45148288 -0.82932284
 -0.28253587 -1.67938632  0.01163317  2.36681103 -0.62768621 -0.35886518
  0.35753966 -1.78180006 -0.91139687  0.36166673  1.81347002  0.29971093
  0.04423431 -0.54301217]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 40ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 41ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 48ms/step
feature of interest:  7


1/1 [==============================] - 0s 43ms/step
feature of interest:  7
shapley value of this feature:  -0.000143213595824632
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 48ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 50ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 48ms/step
feature of interest:  10
shapley value of this feature:  1.5893415956382164e-06
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 45ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 35ms/step
the current coalition:  [7, 10]
weight

...

1/1 [==============================] - 0s 47ms/step
feature of interest:  16
shapley value of this feature:  -6.710528145538783e-05
--------
--------
selected instance:  [-0.05133718 -0.14356403 -0.48666964 -0.44864712 -0.16509766  0.02154541
  0.13868909  1.25521224 -0.11058033 -0.1879656  -0.88362789 -0.84664186
 -0.92216773 -0.7494076  -0.67967275  0.2099406  -0.28675759  0.01478256
 -0.76259956 -0.06356197]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 39ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 55ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 63ms/step
feature of interest:  7
shapley value of this feature:  0.0009858354789951044
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
w

1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 48ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  10
shapley value of this feature:  -3.228360596412452e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 46ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 40ms/step
feature of interest:  16
shapley value of this feature:  0.0013574121347546837
--------
--------
selected instance:  [ 1.19720184 -0.85923865  1.95360342  0.54199

1/1 [==============================] - 0s 46ms/step
feature of interest:  16
shapley value of this feature:  -0.00010064744973304676
--------
--------
selected instance:  [ 0.57338871 -0.56786822 -0.74452501 -1.93980117 -0.96518789  0.58914792
 -0.26107196  0.28547165 -0.11012767 -0.1879656   0.4758018   0.57244261
  0.02405995  0.03999724 -0.18781175  0.22836399  0.25200333  0.34280375
 -0.76259956  0.59078493]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 64ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  0.00012505468340557918
--------
--------
Index of feature of interest:  10
the current coalition:  [7]

1/1 [==============================] - 0s 47ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 47ms/step
feature of interest:  10
shapley value of this feature:  5.0611389332521806e-06
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 33ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 48ms/step
feature of interest:  16
shapley value of this feature:  -4.904233039035434e-05
--------
--------
selected instance:  [-2.4115449   0.21162394 -0.26012331 -0.1047634   3.80490326  0.85508369
 -0.03127235  1.15787233 -0.11056371 -0.18796561  1.27938527  1.71849551
  0.55528609 -1.23926908 -0

1/1 [==============================] - 0s 49ms/step
feature of interest:  16
shapley value of this feature:  -0.00013883918256918238
--------
--------


In [81]:
all_sample = pd.concat([sample_to_explain[0], sample_to_explain[1]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[2]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[3]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[4]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[5]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[6]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[7]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[8]], ignore_index=True)

all_sample

In [90]:
shapleydf = pd.DataFrame(shapley_value_all, columns = ['feature: dolvol', 'feature: baspred', 'feature: sp'])
shapley_mtx = pd.concat([all_sample, shapleydf], axis=1)

shapley_mtx

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0   0.528448 -0.064917  0.224326 -1.483216 -0.168396 -0.440080 -0.250366   
1   0.113065 -1.303000  0.943732 -0.797343  7.760554 -0.459020 -0.278573   
2   1.100338  0.380716 -0.897756 -0.299539  0.443509  0.391001 -0.199949   
3  -1.422809 -0.984736  0.637894 -0.580499  5.650364  1.841581 -0.275316   
4  -0.574709 -0.112385  0.772665 -0.124691 -0.451483 -0.829323 -0.282536   
..       ...       ...       ...       ...       ...       ...       ...   
85  0.092011 -0.344763 -0.478638 -1.058499 -0.615742 -0.729530 -0.278275   
86  1.197202 -0.859239  1.953603  0.541995  0.968625 -0.572433 -0.280739   
87  0.573389 -0.567868 -0.744525 -1.939801 -0.965188  0.589148 -0.261072   
88  0.172675  0.017609 -0.035974  0.670903 -0.078735  0.106603 -0.099266   
89 -2.411545  0.211624 -0.260123 -0.104763  3.804903  0.855084 -0.031272   

      dolvol       ill  zerotrade  ...      beta    betasq        ep  \
0  -0.108141 -0.110149  -0.187966  ... -0.573710 -0.593793  0.284879   
1  -0.721168 -0.106765  -0.187966  ...  0.230915 -0.027903 -0.119240   
2   0.641119 -0.110561  -0.187966  ... -0.638695 -0.627131  0.230165   
3   0.134645 -0.110030  -0.187966  ... -0.944191 -0.759092  0.562626   
4  -1.679386  0.011633   2.366811  ... -1.781800 -0.911397  0.361667   
..       ...       ...        ...  ...       ...       ...       ...   
85 -0.920163 -0.099033  -0.187966  ...  0.367081  0.095893  0.135968   
86 -0.966251 -0.098166  -0.187966  ...  0.105168 -0.135019  0.443541   
87  0.285472 -0.110128  -0.187966  ...  0.039997 -0.187812  0.228364   
88  0.841470 -0.110575  -0.187966  ... -0.226886 -0.384614  0.165091   
89  1.157872 -0.110564  -0.187966  ... -1.239269 -0.847776  0.130021   

          sp       agr     nincr  return(t-1)  feature: dolvol  \
0  -0.065209  0.290871 -0.762600     0.471608        -0.000002   
1   0.389670  0.668641  0.044234     0.118166         0.000011   
2  -0.253073  0.062293 -0.762600     0.972061         0.000010   
3   0.089930 -0.537117 -0.762600    -1.424857         0.000130   
4   1.813470  0.299711  0.044234    -0.543012        -0.000091   
..       ...       ...       ...          ...              ...   
85 -0.117169  0.301179  0.044234     0.101921        -0.000014   
86 -0.337588 -2.214031 -0.762600     1.038136         0.000173   
87  0.252003  0.342804 -0.762600     0.590785         0.000125   
88 -0.449386  0.035293 -0.762600     0.140076        -0.000054   
89 -0.383945  0.266261  2.464736    -2.393664         0.000183   

    feature: baspred  feature: sp  
0           0.000040    -0.000038  
1          -0.000086    -0.000019  
2          -0.000063     0.000063  
3           0.000021    -0.000017  
4           0.000017     0.000048  
..               ...          ...  
85         -0.000032     0.001357  
86         -0.000199    -0.000101  
87          0.000366    -0.000034  
88          0.000005    -0.000049  
89          0.000137    -0.000139  

[90 rows x 23 columns]

In [91]:
shapleymtxes = list()

In [92]:
shapleymtxes.append(shapley_mtx)

**model 2**

In [93]:
# load model into obj model
model = models_NN[1]


M = 10  # the number of random samples to calculate marginal contribution from
n_features = len(bins[0].columns)
feature_idxs = [7, 10, 16]
sample_to_explain = list()
shapley_value_all = list()


for df in bins:  # for each bin
    samplex = df.sample(10)  # sample 10 rows
    sample_to_explain.append(samplex)  # append them to a list
    xarray = samplex.values   # convert them to array
    
    for i in range(10):
        x = xarray[i]  # set x as the instance of interest aka the sample of index i
        print("selected instance: ", x)  # print out the instance of interest
        shapley_values = []

        for i in range(3):   # for each feature of interest
            x_idx = [7, 10, 16]
            marg_contri_feature = []

            feature_of_interest = feature_idxs[i]  # select the feature we are examining
            print("Index of feature of interest: ", feature_of_interest)
            x_idx.remove(feature_of_interest)  # the rest of the features we are about to examine

            all_combinations = []  # all coalitions of features minus the feature of interest
            for r in range(1, len(x_idx) + 1):   # generate combinations of features
                combinations_of_length_r = list(combinations(x_idx, r))
                all_combinations.extend(combinations_of_length_r)

            for coalition in all_combinations:  # for each coalition
                coalition = list(coalition)
                print('the current coalition: ', coalition)
                weight = math.factorial(len(coalition)) * math.factorial(n_features - len(coalition)-1)/ math.factorial(n_features)
                print("weight of this coalition: ", weight)

                marg_contri_coalition = []  # marginal contributions of this coalition

                for _ in range(M):
                    z = df.sample(1).values[0]  # random select sample    

                    # construct two new instances
                    x_orig = np.array([x[i] if i in coalition + [feature_of_interest] else z[i] for i in range(n_features)])
                    x_rando = np.array([x[i] if i in coalition else z[i] for i in range(n_features)])             

                    # calculate marginal contribution
                    marginal_contribution = model.predict(x_orig.reshape(1, -1))[0][0] - model.predict(x_rando.reshape(1, -1))[0][0]
                    marg_contri_coalition.append(marginal_contribution)

                sigma_j = sum(marg_contri_coalition) / len(marg_contri_coalition)
                shapley_coalition = sigma_j*weight  # for one coaltion examined for feature of interest
                marg_contri_feature.append(shapley_coalition)

            shapley_j = sum(marg_contri_feature)  # shapley value of feature j
            shapley_values.append(shapley_j)

            print("feature of interest: ", feature_of_interest)
            print("shapley value of this feature: ", shapley_j)
            print('--------')
            print('--------')
        shapley_value_all.append(shapley_values)

selected instance:  [ 0.30371927 -0.08707697 -0.4904705  -1.11454397 -0.14223986 -0.46460825
 -0.24439405 -0.06837699 -0.11027559 -0.18796558 -0.6643243  -0.75334345
 -0.72058784 -0.64730306 -0.63140884  0.33763141 -0.07111846 -0.07722769
 -0.76259956  0.26184917]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 50ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 56ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  7
shapley value of this feature:  -5.972059688677913e-06
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 72ms/step
the current coalition:  [16]
weight of this coalit

1/1 [==============================] - 0s 47ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 47ms/step
feature of interest:  10
shapley value of this feature:  -0.00016166508502778952
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 40ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 40ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 40ms/step
feature of interest:  16
shapley value of this feature:  4.676142418811544e-05
--------
--------
selected instance:  [-3.02031792  9.6910469   0.21453252  4.02661453 -0.53357793  2.33028705
 -0.27387758  0.61645136 -0.11032921 -0.18796561  1.81834857  1.39431372
  0.82495728 -1.61745699 -0

1/1 [==============================] - 0s 42ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 61ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 47ms/step
feature of interest:  7
shapley value of this feature:  6.86721081099315e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 48ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  10
shapley value of this feature:  1.2916730912892437e-06
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weig

1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 38ms/step
feature of interest:  16
shapley value of this feature:  -9.40023491169974e-06
--------
--------
selected instance:  [ 0.68494353  0.00342318 -0.11921186 -0.84085304  0.03165766 -0.31854911
 -0.24793526  0.05933783 -0.11014383 -0.18796559 -0.67000091 -0.6655064
 -0.63915699 -0.60796447 -0.61159635  0.28487916 -0.06520946  0.29087103
  0.04423431  0.5972975 ]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 44ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 48ms/step
feature of interest:  7
sha

1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  6.301509129286509e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 44ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 22ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 34ms/step
feature of interest:  10
shapley value of this feature:  -7.321792028365079e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [7, 10]
weight

...

1/1 [==============================] - 0s 34ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  16
shapley value of this feature:  0.0004493690105100647
--------
--------
selected instance:  [-0.23400655 -0.09610982 -0.45158795 -0.15808249  0.29923653 -0.11107956
 -0.01029694  0.95083905 -0.11056327 -0.1879656  -0.60686872 -0.50365007
 -0.79847246  0.45004552  0.17529782  0.16821272 -0.42853168 -0.64590194
 -0.76259956 -0.21952289]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 27ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 34ms/step
feature of interest:  7
sh

1/1 [==============================] - 0s 41ms/step
feature of interest:  10
shapley value of this feature:  -0.00011585128411912081
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 39ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 36ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  16
shapley value of this feature:  1.2434090961489761e-05
--------
--------
selected instance:  [-0.16551371 -0.16708954  1.39000219 -0.36141012 -0.21979104 -0.06819561
 -0.2171835   0.31220993 -0.11019802 -0.18796558  0.71318383  0.92808869
  1.27635929 -1.18550561 -0.83445607  0.10756475 -0.46992185  0.00812651
 -0.76259956 -0.08276609]
Index of feature of interest:  7
the current coalition:  [10]

1/1 [==============================] - 0s 28ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 44ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 35ms/step
feature of interest:  7
shapley value of this feature:  -1.1802054288094505e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 36ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 37ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 36ms/step
feature of interest:  10
shapley value of this feature:  3.8812788290499954e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
w

1/1 [==============================] - 0s 47ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 28ms/step
feature of interest:  16
shapley value of this feature:  -9.699035174491112e-05
--------
--------
selected instance:  [-0.39109684 -0.78236808  0.47120179 -1.04184335 -0.51583756 -0.77832854
 -0.27784935 -0.98018238 -0.08448478 -0.18796554  0.34046696  0.1342434
 -0.0577605  -0.78590069 -0.69581601 -0.17668689 -0.54246209  0.83975357
 -0.76259956 -0.32876443]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 23ms/step
feature of interest:  7
sh

1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 33ms/step
feature of interest:  10
shapley value of this feature:  0.0004167513949905484
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 48ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 34ms/step
feature of interest:  16
shapley value of this feature:  -7.018957243502487e-06
--------
--------


In [94]:
all_sample = pd.concat([sample_to_explain[0], sample_to_explain[1]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[2]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[3]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[4]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[5]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[6]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[7]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[8]], ignore_index=True)

all_sample

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0   0.303719 -0.087077 -0.490470 -1.114544 -0.142240 -0.464608 -0.244394   
1  -0.238017  0.057455 -0.220157  0.183782  1.013223 -0.452680 -0.278016   
2  -3.020318  9.691047  0.214533  4.026615 -0.533578  2.330287 -0.273878   
3   0.352285  1.595635 -0.682101  0.681915  1.537728  4.629042 -0.253905   
4   0.684944  0.003423 -0.119212 -0.840853  0.031658 -0.318549 -0.247935   
..       ...       ...       ...       ...       ...       ...       ...   
85 -0.234007 -0.096110 -0.451588 -0.158082  0.299237 -0.111080 -0.010297   
86 -0.165514 -0.167090  1.390002 -0.361410 -0.219791 -0.068196 -0.217184   
87  0.148620 -0.138328  0.621799  0.059567  0.627278  0.501708 -0.152577   
88 -0.391097 -0.782368  0.471202 -1.041843 -0.515838 -0.778329 -0.277849   
89  0.219762 -0.518755  0.850207 -0.506000 -0.726584 -0.577535 -0.278626   

      dolvol       ill  zerotrade  baspread    retvol   idiovol      beta  \
0  -0.068377 -0.110276  -0.187966 -0.664324 -0.753343 -0.720588 -0.647303   
1  -0.684456 -0.107015  -0.187966 -0.559274 -0.543799  0.873356  0.166128   
2   0.616451 -0.110329  -0.187966  1.818349  1.394314  0.824957 -1.617457   
3   0.725098 -0.110485  -0.187966  0.746948  0.470676  0.177129  0.273009   
4   0.059338 -0.110144  -0.187966 -0.670001 -0.665506 -0.639157 -0.607964   
..       ...       ...        ...       ...       ...       ...       ...   
85  0.950839 -0.110563  -0.187966 -0.606869 -0.503650 -0.798472  0.450046   
86  0.312210 -0.110198  -0.187966  0.713184  0.928089  1.276359 -1.185506   
87  0.781928 -0.110557  -0.187966 -0.301208 -0.133710 -0.367144 -0.843782   
88 -0.980182 -0.084485  -0.187966  0.340467  0.134243 -0.057761 -0.785901   
89 -0.819630 -0.101336  -0.187966  1.297884  0.480074  1.700181  3.697116   

      betasq        ep        sp       agr     nincr  return(t-1)  
0  -0.631409  0.337631 -0.071118 -0.077228 -0.762600     0.261849  
1  -0.083955 -0.119240  0.389670  0.668641  0.044234    -0.226478  
2  -0.905724  0.581350  1.918343  0.260226  0.044234    -3.330430  
3   0.009501  0.366146  0.164642 -0.127828  0.044234     0.384609  
4  -0.611596  0.284879 -0.065209  0.290871  0.044234     0.597298  
..       ...       ...       ...       ...       ...          ...  
85  0.175298  0.168213 -0.428532 -0.645902 -0.762600    -0.219523  
86 -0.834456  0.107565 -0.469922  0.008127 -0.762600    -0.082766  
87 -0.720226  0.130131 -0.542127  0.512028  0.044234     0.152289  
88 -0.695816 -0.176687 -0.542462  0.839754 -0.762600    -0.328764  
89  5.649007 -0.141572 -0.587019  0.891441 -0.762600     0.257672  

[90 rows x 20 columns]

In [95]:
shapleydf = pd.DataFrame(shapley_value_all, columns = ['feature: dolvol', 'feature: baspred', 'feature: sp'])
shapley_mtx = pd.concat([all_sample, shapleydf], axis=1)
shapleymtxes.append(shapley_mtx)

shapley_mtx

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0   0.303719 -0.087077 -0.490470 -1.114544 -0.142240 -0.464608 -0.244394   
1  -0.238017  0.057455 -0.220157  0.183782  1.013223 -0.452680 -0.278016   
2  -3.020318  9.691047  0.214533  4.026615 -0.533578  2.330287 -0.273878   
3   0.352285  1.595635 -0.682101  0.681915  1.537728  4.629042 -0.253905   
4   0.684944  0.003423 -0.119212 -0.840853  0.031658 -0.318549 -0.247935   
..       ...       ...       ...       ...       ...       ...       ...   
85 -0.234007 -0.096110 -0.451588 -0.158082  0.299237 -0.111080 -0.010297   
86 -0.165514 -0.167090  1.390002 -0.361410 -0.219791 -0.068196 -0.217184   
87  0.148620 -0.138328  0.621799  0.059567  0.627278  0.501708 -0.152577   
88 -0.391097 -0.782368  0.471202 -1.041843 -0.515838 -0.778329 -0.277849   
89  0.219762 -0.518755  0.850207 -0.506000 -0.726584 -0.577535 -0.278626   

      dolvol       ill  zerotrade  ...      beta    betasq        ep  \
0  -0.068377 -0.110276  -0.187966  ... -0.647303 -0.631409  0.337631   
1  -0.684456 -0.107015  -0.187966  ...  0.166128 -0.083955 -0.119240   
2   0.616451 -0.110329  -0.187966  ... -1.617457 -0.905724  0.581350   
3   0.725098 -0.110485  -0.187966  ...  0.273009  0.009501  0.366146   
4   0.059338 -0.110144  -0.187966  ... -0.607964 -0.611596  0.284879   
..       ...       ...        ...  ...       ...       ...       ...   
85  0.950839 -0.110563  -0.187966  ...  0.450046  0.175298  0.168213   
86  0.312210 -0.110198  -0.187966  ... -1.185506 -0.834456  0.107565   
87  0.781928 -0.110557  -0.187966  ... -0.843782 -0.720226  0.130131   
88 -0.980182 -0.084485  -0.187966  ... -0.785901 -0.695816 -0.176687   
89 -0.819630 -0.101336  -0.187966  ...  3.697116  5.649007 -0.141572   

          sp       agr     nincr  return(t-1)  feature: dolvol  \
0  -0.071118 -0.077228 -0.762600     0.261849        -0.000006   
1   0.389670  0.668641  0.044234    -0.226478         0.000023   
2   1.918343  0.260226  0.044234    -3.330430        -0.000026   
3   0.164642 -0.127828  0.044234     0.384609         0.000069   
4  -0.065209  0.290871  0.044234     0.597298        -0.000121   
..       ...       ...       ...          ...              ...   
85 -0.428532 -0.645902 -0.762600    -0.219523        -0.000260   
86 -0.469922  0.008127 -0.762600    -0.082766        -0.000395   
87 -0.542127  0.512028  0.044234     0.152289        -0.000012   
88 -0.542462  0.839754 -0.762600    -0.328764         0.000402   
89 -0.587019  0.891441 -0.762600     0.257672         0.000043   

    feature: baspred  feature: sp  
0          -0.000038    -0.000008  
1          -0.000162     0.000047  
2          -0.000103    -0.000132  
3           0.000001    -0.000009  
4           0.000168     0.000022  
..               ...          ...  
85         -0.000116     0.000012  
86         -0.000177    -0.000395  
87          0.000039    -0.000097  
88          0.000417    -0.000273  
89          0.000417    -0.000007  

[90 rows x 23 columns]

**model 3**

In [96]:
# load model into obj model
model = models_NN[2]


M = 10  # the number of random samples to calculate marginal contribution from
n_features = len(bins[0].columns)
feature_idxs = [7, 10, 16]
sample_to_explain = list()
shapley_value_all = list()


for df in bins:  # for each bin
    samplex = df.sample(10)  # sample 10 rows
    sample_to_explain.append(samplex)  # append them to a list
    xarray = samplex.values   # convert them to array
    
    for i in range(10):
        x = xarray[i]  # set x as the instance of interest aka the sample of index i
        print("selected instance: ", x)  # print out the instance of interest
        shapley_values = []

        for i in range(3):   # for each feature of interest
            x_idx = [7, 10, 16]
            marg_contri_feature = []

            feature_of_interest = feature_idxs[i]  # select the feature we are examining
            print("Index of feature of interest: ", feature_of_interest)
            x_idx.remove(feature_of_interest)  # the rest of the features we are about to examine

            all_combinations = []  # all coalitions of features minus the feature of interest
            for r in range(1, len(x_idx) + 1):   # generate combinations of features
                combinations_of_length_r = list(combinations(x_idx, r))
                all_combinations.extend(combinations_of_length_r)

            for coalition in all_combinations:  # for each coalition
                coalition = list(coalition)
                print('the current coalition: ', coalition)
                weight = math.factorial(len(coalition)) * math.factorial(n_features - len(coalition)-1)/ math.factorial(n_features)
                print("weight of this coalition: ", weight)

                marg_contri_coalition = []  # marginal contributions of this coalition

                for _ in range(M):
                    z = df.sample(1).values[0]  # random select sample    

                    # construct two new instances
                    x_orig = np.array([x[i] if i in coalition + [feature_of_interest] else z[i] for i in range(n_features)])
                    x_rando = np.array([x[i] if i in coalition else z[i] for i in range(n_features)])             

                    # calculate marginal contribution
                    marginal_contribution = model.predict(x_orig.reshape(1, -1))[0][0] - model.predict(x_rando.reshape(1, -1))[0][0]
                    marg_contri_coalition.append(marginal_contribution)

                sigma_j = sum(marg_contri_coalition) / len(marg_contri_coalition)
                shapley_coalition = sigma_j*weight  # for one coaltion examined for feature of interest
                marg_contri_feature.append(shapley_coalition)

            shapley_j = sum(marg_contri_feature)  # shapley value of feature j
            shapley_values.append(shapley_j)

            print("feature of interest: ", feature_of_interest)
            print("shapley value of this feature: ", shapley_j)
            print('--------')
            print('--------')
        shapley_value_all.append(shapley_values)

selected instance:  [-0.63217116  2.34609975 -2.83381346  2.75293431  1.13297556  1.62094033
 -0.27486441  0.25260945 -0.11021128 -0.1879656   0.24794949 -0.42920256
  1.05310263 -0.95341145 -0.76243956  0.58078067  1.918343    0.26022588
  1.65790206 -0.60615078]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 30ms/step
feature of interest:  7
shapley value of this feature:  7.299892702384999e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coaliti

1/1 [==============================] - 0s 47ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 78ms/step
feature of interest:  10
shapley value of this feature:  -6.944057090502036e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 48ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 62ms/step
feature of interest:  16
shapley value of this feature:  0.00020577672882582883
--------
--------
selected instance:  [ 0.35450991  0.52176513 -0.77799593 -0.7134747   0.668807    1.45958474
 -0.18344475  0.90012181 -0.11053903 -0.1879656   0.05444482 -0.18575362
 -0.23526802 -0.64735637 -0

1/1 [==============================] - 0s 30ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  7
shapley value of this feature:  -4.76639599087294e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 39ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 47ms/step
feature of interest:  10
shapley value of this feature:  -0.00023647836758074355
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
we

1/1 [==============================] - 0s 26ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  16
shapley value of this feature:  8.052762706725918e-05
--------
--------
selected instance:  [ 0.60936985  2.76663262 -0.54942148  1.46570161 -0.72433002  1.9290203
 -0.26614429  0.41191824 -0.11014956 -0.18796561  1.91844975  2.01622153
  0.07851068 -0.20377202 -0.36880262  0.04347023  0.56649873 -0.21161655
  0.04423431  0.8734437 ]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7
sha

1/1 [==============================] - 0s 48ms/step
feature of interest:  7
shapley value of this feature:  -5.296373413058749e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 33ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  10
shapley value of this feature:  -9.118210655032542e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 35ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weigh

...

1/1 [==============================] - 0s 32ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 30ms/step
feature of interest:  16
shapley value of this feature:  1.5025041229500074e-05
--------
--------
selected instance:  [ 0.1052958   0.04910154 -0.2744728   0.16861045 -0.0242108   0.42078964
 -0.25806528  0.23326848 -0.11035952 -0.1879656  -0.82167348 -0.77391886
 -0.60542327 -0.12793973 -0.31528611  0.18358258 -0.35819368 -0.13074513
  0.85106818  0.08355113]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 33ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16

1/1 [==============================] - 0s 33ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  -0.00020422384818220696
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 34ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 29ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  10
shapley value of this feature:  -0.0008390004043494574
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 36ms/step
the current coalition:  [10]
w

1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 39ms/step
feature of interest:  7
shapley value of this feature:  0.00014617503588006163
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 21ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 35ms/step
feature of interest:  10
shapley value of this feature:  -0.0008888579206813498
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
we

1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  16
shapley value of this feature:  -2.571711657100427e-05
--------
--------
selected instance:  [ 0.30221927 -0.0106692   0.20794431  0.64851214 -0.86687148  0.84206895
 -0.19358679  0.78491682 -0.11055878 -0.1879656  -0.82683133 -0.78926752
 -0.34896207 -0.5582821  -0.58560658 -0.3717437  -0.36867481  1.0029123
 -0.76259956  0.2602319 ]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 22ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7
sh

1/1 [==============================] - 0s 33ms/step
feature of interest:  10
shapley value of this feature:  -8.297217356269821e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 40ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 36ms/step
feature of interest:  16
shapley value of this feature:  4.3111661046046265e-05
--------
--------
selected instance:  [-0.93954198 -0.01914259  0.2781296   0.26852909 -0.47986968 -0.0456729
 -0.22914832  0.3362239  -0.11034267 -0.1879656   0.30554562  0.57381097
  1.42429076 -1.2523041  -0.85081434  0.10756475 -0.46992185  0.00421117
 -0.76259956 -0.84180733]
Index of feature of interest:  7
the current coalition:  [10]
w

In [97]:
all_sample = pd.concat([sample_to_explain[0], sample_to_explain[1]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[2]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[3]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[4]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[5]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[6]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[7]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[8]], ignore_index=True)

all_sample

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0  -0.632171  2.346100 -2.833813  2.752934  1.132976  1.620940 -0.274864   
1   1.184785  1.419865 -0.437116 -0.125594  1.715883  4.665173 -0.249384   
2   0.354510  0.521765 -0.777996 -0.713475  0.668807  1.459585 -0.183445   
3  -0.346001  2.035778 -1.102990  0.703922  0.440209  2.975842 -0.253553   
4   0.609370  2.766633 -0.549421  1.465702 -0.724330  1.929020 -0.266144   
..       ...       ...       ...       ...       ...       ...       ...   
85  0.105296  0.049102 -0.274473  0.168610 -0.024211  0.420790 -0.258065   
86  0.336664 -0.654439 -0.411555 -0.720712  0.371837  0.178827  0.229047   
87 -0.093663 -0.303102 -0.262865  2.476480 -1.131780 -0.857041 -0.282726   
88  0.302219 -0.010669  0.207944  0.648512 -0.866871  0.842069 -0.193587   
89 -0.939542 -0.019143  0.278130  0.268529 -0.479870 -0.045673 -0.229148   

      dolvol       ill  zerotrade  baspread    retvol   idiovol      beta  \
0   0.252609 -0.110211  -0.187966  0.247949 -0.429203  1.053103 -0.953411   
1   0.828503 -0.110526  -0.187966  0.940199  0.783308  0.228838  0.184309   
2   0.900122 -0.110539  -0.187966  0.054445 -0.185754 -0.235268 -0.647356   
3   0.663251 -0.110457  -0.187966  1.847983  1.683005  0.100948  0.466954   
4   0.411918 -0.110150  -0.187966  1.918450  2.016222  0.078511 -0.203772   
..       ...       ...        ...       ...       ...       ...       ...   
85  0.233268 -0.110360  -0.187966 -0.821673 -0.773919 -0.605423 -0.127940   
86  1.282060 -0.110585  -0.187966 -0.812034 -0.761318 -1.010724 -0.454504   
87 -1.854797  0.010640  -0.187965  0.159272 -0.009287  0.568084 -0.956689   
88  0.784917 -0.110559  -0.187966 -0.826831 -0.789268 -0.348962 -0.558282   
89  0.336224 -0.110343  -0.187966  0.305546  0.573811  1.424291 -1.252304   

      betasq        ep        sp       agr     nincr  return(t-1)  
0  -0.762440  0.580781  1.918343  0.260226  1.657902    -0.606151  
1  -0.068411  0.366146  0.164642 -0.127828  0.044234     1.126412  
2  -0.631435  0.214134 -0.365382 -0.110737  0.044234     0.332842  
3   0.191850  0.366146  0.164642 -0.127828 -0.762600    -0.111913  
4  -0.368803  0.043470  0.566499 -0.211617  0.044234     0.873444  
..       ...       ...       ...       ...       ...          ...  
85 -0.315286  0.183583 -0.358194 -0.130745  0.851068     0.083551  
86 -0.527833  0.212581 -0.362776  0.213789  0.044234     0.293331  
87 -0.763621  0.177566  0.015407  1.237907 -0.762600    -0.061067  
88 -0.585607 -0.371744 -0.368675  1.002912 -0.762600     0.260232  
89 -0.850814  0.107565 -0.469922  0.004211 -0.762600    -0.841807  

[90 rows x 20 columns]

In [98]:
shapleydf = pd.DataFrame(shapley_value_all, columns = ['feature: dolvol', 'feature: baspred', 'feature: sp'])
shapley_mtx = pd.concat([all_sample, shapleydf], axis=1)
shapleymtxes.append(shapley_mtx)

shapley_mtx

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0  -0.632171  2.346100 -2.833813  2.752934  1.132976  1.620940 -0.274864   
1   1.184785  1.419865 -0.437116 -0.125594  1.715883  4.665173 -0.249384   
2   0.354510  0.521765 -0.777996 -0.713475  0.668807  1.459585 -0.183445   
3  -0.346001  2.035778 -1.102990  0.703922  0.440209  2.975842 -0.253553   
4   0.609370  2.766633 -0.549421  1.465702 -0.724330  1.929020 -0.266144   
..       ...       ...       ...       ...       ...       ...       ...   
85  0.105296  0.049102 -0.274473  0.168610 -0.024211  0.420790 -0.258065   
86  0.336664 -0.654439 -0.411555 -0.720712  0.371837  0.178827  0.229047   
87 -0.093663 -0.303102 -0.262865  2.476480 -1.131780 -0.857041 -0.282726   
88  0.302219 -0.010669  0.207944  0.648512 -0.866871  0.842069 -0.193587   
89 -0.939542 -0.019143  0.278130  0.268529 -0.479870 -0.045673 -0.229148   

      dolvol       ill  zerotrade  ...      beta    betasq        ep  \
0   0.252609 -0.110211  -0.187966  ... -0.953411 -0.762440  0.580781   
1   0.828503 -0.110526  -0.187966  ...  0.184309 -0.068411  0.366146   
2   0.900122 -0.110539  -0.187966  ... -0.647356 -0.631435  0.214134   
3   0.663251 -0.110457  -0.187966  ...  0.466954  0.191850  0.366146   
4   0.411918 -0.110150  -0.187966  ... -0.203772 -0.368803  0.043470   
..       ...       ...        ...  ...       ...       ...       ...   
85  0.233268 -0.110360  -0.187966  ... -0.127940 -0.315286  0.183583   
86  1.282060 -0.110585  -0.187966  ... -0.454504 -0.527833  0.212581   
87 -1.854797  0.010640  -0.187965  ... -0.956689 -0.763621  0.177566   
88  0.784917 -0.110559  -0.187966  ... -0.558282 -0.585607 -0.371744   
89  0.336224 -0.110343  -0.187966  ... -1.252304 -0.850814  0.107565   

          sp       agr     nincr  return(t-1)  feature: dolvol  \
0   1.918343  0.260226  1.657902    -0.606151         0.000073   
1   0.164642 -0.127828  0.044234     1.126412         0.000048   
2  -0.365382 -0.110737  0.044234     0.332842        -0.000092   
3   0.164642 -0.127828 -0.762600    -0.111913        -0.000048   
4   0.566499 -0.211617  0.044234     0.873444        -0.000023   
..       ...       ...       ...          ...              ...   
85 -0.358194 -0.130745  0.851068     0.083551         0.000035   
86 -0.362776  0.213789  0.044234     0.293331        -0.000204   
87  0.015407  1.237907 -0.762600    -0.061067         0.000146   
88 -0.368675  1.002912 -0.762600     0.260232        -0.000118   
89 -0.469922  0.004211 -0.762600    -0.841807        -0.000019   

    feature: baspred  feature: sp  
0          -0.000054     0.000122  
1          -0.000069     0.000206  
2           0.000001     0.000060  
3          -0.000236     0.000081  
4           0.000213     0.000021  
..               ...          ...  
85         -0.000469    -0.000025  
86         -0.000839     0.000024  
87         -0.000889    -0.000026  
88         -0.000083     0.000043  
89          0.000432     0.000832  

[90 rows x 23 columns]

**model 4**

In [99]:
# load model into obj model
model = models_NN[3]


M = 10  # the number of random samples to calculate marginal contribution from
n_features = len(bins[0].columns)
feature_idxs = [7, 10, 16]
sample_to_explain = list()
shapley_value_all = list()


for df in bins:  # for each bin
    samplex = df.sample(10)  # sample 10 rows
    sample_to_explain.append(samplex)  # append them to a list
    xarray = samplex.values   # convert them to array
    
    for i in range(10):
        x = xarray[i]  # set x as the instance of interest aka the sample of index i
        print("selected instance: ", x)  # print out the instance of interest
        shapley_values = []

        for i in range(3):   # for each feature of interest
            x_idx = [7, 10, 16]
            marg_contri_feature = []

            feature_of_interest = feature_idxs[i]  # select the feature we are examining
            print("Index of feature of interest: ", feature_of_interest)
            x_idx.remove(feature_of_interest)  # the rest of the features we are about to examine

            all_combinations = []  # all coalitions of features minus the feature of interest
            for r in range(1, len(x_idx) + 1):   # generate combinations of features
                combinations_of_length_r = list(combinations(x_idx, r))
                all_combinations.extend(combinations_of_length_r)

            for coalition in all_combinations:  # for each coalition
                coalition = list(coalition)
                print('the current coalition: ', coalition)
                weight = math.factorial(len(coalition)) * math.factorial(n_features - len(coalition)-1)/ math.factorial(n_features)
                print("weight of this coalition: ", weight)

                marg_contri_coalition = []  # marginal contributions of this coalition

                for _ in range(M):
                    z = df.sample(1).values[0]  # random select sample    

                    # construct two new instances
                    x_orig = np.array([x[i] if i in coalition + [feature_of_interest] else z[i] for i in range(n_features)])
                    x_rando = np.array([x[i] if i in coalition else z[i] for i in range(n_features)])             

                    # calculate marginal contribution
                    marginal_contribution = model.predict(x_orig.reshape(1, -1))[0][0] - model.predict(x_rando.reshape(1, -1))[0][0]
                    marg_contri_coalition.append(marginal_contribution)

                sigma_j = sum(marg_contri_coalition) / len(marg_contri_coalition)
                shapley_coalition = sigma_j*weight  # for one coaltion examined for feature of interest
                marg_contri_feature.append(shapley_coalition)

            shapley_j = sum(marg_contri_feature)  # shapley value of feature j
            shapley_values.append(shapley_j)

            print("feature of interest: ", feature_of_interest)
            print("shapley value of this feature: ", shapley_j)
            print('--------')
            print('--------')
        shapley_value_all.append(shapley_values)

selected instance:  [-0.5094643  -1.23457576 -0.92855643 -0.87070982  5.41482837  0.43948136
 -0.27830711 -0.28395538 -0.10847909 -0.1879656   0.51481859  0.37965767
  1.02628702 -0.56576484 -0.58959003  0.56578987  0.08993024 -0.5371169
 -0.76259956 -0.42844743]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  7.035502899786708e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 34ms/step
the current coalition:  [16]
weight of this coalitio

1/1 [==============================] - 0s 25ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 33ms/step
feature of interest:  10
shapley value of this feature:  0.0001061774433280031
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 34ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 28ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 21ms/step
feature of interest:  16
shapley value of this feature:  5.039950663888315e-05
--------
--------
selected instance:  [-0.08833341 -0.25836733 -0.21533521 -1.6150559  -0.52343432 -0.06469844
 -0.20443694  0.54642607 -0.11051665 -0.1879656  -0.43411821 -0.52104531
 -0.57068493 -0.78187661 -0.6

1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 34ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 34ms/step
feature of interest:  7
shapley value of this feature:  9.16705621210368e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  10
shapley value of this feature:  -7.023814850492261e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weig

1/1 [==============================] - 0s 46ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  16
shapley value of this feature:  -2.66967925150492e-05
--------
--------
selected instance:  [-4.56971458e-01 -3.71018770e-01  2.22716577e-04 -5.94436675e-01
 -2.79817944e-01  1.83964726e-01 -2.08885290e-01  5.03449707e-01
 -1.10522924e-01 -1.87965604e-01 -3.97220576e-01 -6.82172029e-01
 -6.06334042e-01 -7.66211511e-01 -6.87178606e-01  2.01602444e-01
 -3.37433841e-01 -1.56396411e-02  4.42343131e-02 -4.43249396e-01]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 21ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.000292397660818713

1/1 [==============================] - 0s 32ms/step
feature of interest:  10
shapley value of this feature:  3.8446913968924195e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 35ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 47ms/step
feature of interest:  16
shapley value of this feature:  5.673492316439835e-05
--------
--------
selected instance:  [-0.11743283  0.26001395  0.37842704 -1.28900547  0.86513724  1.73058801
 -0.18338599  0.93663616 -0.11056345 -0.18796561  0.22438734  0.45174721
 -0.35000009 -0.71768768 -0.66516754  0.23016463 -0.25307307  0.06229291
  0.85106818 -0.04541669]
Index of feature of interest:  7
the current coalition:  [10]
w

...

1/1 [==============================] - 0s 32ms/step
feature of interest:  16
shapley value of this feature:  -1.651928542258099e-05
--------
--------
selected instance:  [ 0.34409152  1.45853003  0.45682674 -0.62178471  3.57378147  1.78727856
 -0.24684207  0.64770186 -0.11050985 -0.18796561  0.18505743 -0.11654321
  0.76835047  0.08328661 -0.15295173 -0.30412123 -0.51075978  0.50888028
  2.46473593  0.32979606]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 42ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  -0.00013188343696644782
--------
--------
Index of feature of interest:  10
the current coalition:  [7]

1/1 [==============================] - 0s 46ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  10
shapley value of this feature:  4.88289976655914e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  16
shapley value of this feature:  0.00043547594288026383
--------
--------
selected instance:  [-4.96714874  0.85666123 -2.23817013 -1.435106

1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  -0.0003027906087199934
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 35ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  10
shapley value of this feature:  -0.001576879718368165
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [10]
wei

1/1 [==============================] - 0s 31ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  16
shapley value of this feature:  -6.459706642648629e-05
--------
--------
selected instance:  [ 1.26717968 -1.18387558  0.34605761 -0.36716191 -0.10668366 -0.54954689
 -0.27693318 -0.79642464 -0.10435963 -0.18796557  0.77807779  0.06247265
  0.88726653  1.41171026  1.31551612  0.00855627 -0.38141976  0.55514706
  0.04423431  1.11840497]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 45ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 35ms/step
the current coalition:  [10, 16

1/1 [==============================] - 0s 33ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  -3.008900248385661e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 35ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 40ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  10
shapley value of this feature:  -0.0004708434641361236
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 36ms/step
the current coalition:  [10]
we

In [100]:
all_sample = pd.concat([sample_to_explain[0], sample_to_explain[1]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[2]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[3]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[4]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[5]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[6]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[7]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[8]], ignore_index=True)

all_sample

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0  -0.509464 -1.234576 -0.928556 -0.870710  5.414828  0.439481 -0.278307   
1   0.101203 -0.701099  0.493331 -1.193949 -0.449810 -0.836801 -0.282597   
2  -0.088333 -0.258367 -0.215335 -1.615056 -0.523434 -0.064698 -0.204437   
3   0.564430 -1.192070  1.238207 -0.797987  6.056146 -0.405796 -0.278035   
4  -0.456971 -0.371019  0.000223 -0.594437 -0.279818  0.183965 -0.208885   
..       ...       ...       ...       ...       ...       ...       ...   
85  0.790949 -0.737889  0.708447 -1.086772  0.873564  0.275809 -0.117450   
86 -4.967149  0.856661 -2.238170 -1.435107 -0.938956  1.300104 -0.270515   
87  0.797635 -0.253650 -1.785011  0.047480 -0.048584 -0.594827 -0.278774   
88  1.267180 -1.183876  0.346058 -0.367162 -0.106684 -0.549547 -0.276933   
89  0.729440  0.902886  0.875476  0.571045 -0.339132 -0.254878 -0.240745   

      dolvol       ill  zerotrade  baspread    retvol   idiovol      beta  \
0  -0.283955 -0.108479  -0.187966  0.514819  0.379658  1.026287 -0.565765   
1  -1.600933  0.178347   1.685537 -0.122925  1.373873  0.357874 -1.732242   
2   0.546426 -0.110517  -0.187966 -0.434118 -0.521045 -0.570685 -0.781877   
3  -0.735322 -0.108606  -0.187966  0.208859 -0.364084  0.909293  0.366571   
4   0.503450 -0.110523  -0.187966 -0.397221 -0.682172 -0.606334 -0.766212   
..       ...       ...        ...       ...       ...       ...       ...   
85  0.803174 -0.110558  -0.187966 -0.394699 -0.120830 -0.589725  0.110348   
86  0.503530 -0.110038  -0.187966  4.920418  4.219517  3.008805 -1.984610   
87 -0.843067 -0.103307  -0.187966  0.686814  0.261998  0.222963 -0.032859   
88 -0.796425 -0.104360  -0.187966  0.778078  0.062473  0.887267  1.411710   
89  0.095103 -0.110314  -0.187966  0.068392 -0.449549  0.099911  1.750264   

      betasq        ep        sp       agr     nincr  return(t-1)  
0  -0.589590  0.565790  0.089930 -0.537117 -0.762600    -0.428447  
1  -0.910931  0.361667  1.813470  0.299711  0.044234     0.252515  
2  -0.694064  0.201602 -0.337434 -0.015640 -0.762600    -0.085290  
3   0.095414 -0.119240  0.389670  0.668641  0.044234     0.507507  
4  -0.687179  0.201602 -0.337434 -0.015640  0.044234    -0.443249  
..       ...       ...       ...       ...       ...          ...  
85 -0.130744  0.338966  0.203644  0.281227 -0.762600     0.714401  
86 -0.888345 -0.185760 -0.588251  0.267934 -0.762600    -6.055507  
87 -0.244630  0.441488  0.004875 -0.005213  0.044234     0.742112  
88  1.315516  0.008556 -0.381420  0.555147  0.044234     1.118405  
89  1.813247 -0.447563 -0.564912  0.916257  0.851068     0.646809  

[90 rows x 20 columns]

In [101]:
shapleydf = pd.DataFrame(shapley_value_all, columns = ['feature: dolvol', 'feature: baspred', 'feature: sp'])
shapley_mtx = pd.concat([all_sample, shapleydf], axis=1)
shapleymtxes.append(shapley_mtx)

shapley_mtx

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0  -0.509464 -1.234576 -0.928556 -0.870710  5.414828  0.439481 -0.278307   
1   0.101203 -0.701099  0.493331 -1.193949 -0.449810 -0.836801 -0.282597   
2  -0.088333 -0.258367 -0.215335 -1.615056 -0.523434 -0.064698 -0.204437   
3   0.564430 -1.192070  1.238207 -0.797987  6.056146 -0.405796 -0.278035   
4  -0.456971 -0.371019  0.000223 -0.594437 -0.279818  0.183965 -0.208885   
..       ...       ...       ...       ...       ...       ...       ...   
85  0.790949 -0.737889  0.708447 -1.086772  0.873564  0.275809 -0.117450   
86 -4.967149  0.856661 -2.238170 -1.435107 -0.938956  1.300104 -0.270515   
87  0.797635 -0.253650 -1.785011  0.047480 -0.048584 -0.594827 -0.278774   
88  1.267180 -1.183876  0.346058 -0.367162 -0.106684 -0.549547 -0.276933   
89  0.729440  0.902886  0.875476  0.571045 -0.339132 -0.254878 -0.240745   

      dolvol       ill  zerotrade  ...      beta    betasq        ep  \
0  -0.283955 -0.108479  -0.187966  ... -0.565765 -0.589590  0.565790   
1  -1.600933  0.178347   1.685537  ... -1.732242 -0.910931  0.361667   
2   0.546426 -0.110517  -0.187966  ... -0.781877 -0.694064  0.201602   
3  -0.735322 -0.108606  -0.187966  ...  0.366571  0.095414 -0.119240   
4   0.503450 -0.110523  -0.187966  ... -0.766212 -0.687179  0.201602   
..       ...       ...        ...  ...       ...       ...       ...   
85  0.803174 -0.110558  -0.187966  ...  0.110348 -0.130744  0.338966   
86  0.503530 -0.110038  -0.187966  ... -1.984610 -0.888345 -0.185760   
87 -0.843067 -0.103307  -0.187966  ... -0.032859 -0.244630  0.441488   
88 -0.796425 -0.104360  -0.187966  ...  1.411710  1.315516  0.008556   
89  0.095103 -0.110314  -0.187966  ...  1.750264  1.813247 -0.447563   

          sp       agr     nincr  return(t-1)  feature: dolvol  \
0   0.089930 -0.537117 -0.762600    -0.428447         0.000070   
1   1.813470  0.299711  0.044234     0.252515         0.000124   
2  -0.337434 -0.015640 -0.762600    -0.085290         0.000039   
3   0.389670  0.668641  0.044234     0.507507         0.000092   
4  -0.337434 -0.015640  0.044234    -0.443249         0.000464   
..       ...       ...       ...          ...              ...   
85  0.203644  0.281227 -0.762600     0.714401        -0.001318   
86 -0.588251  0.267934 -0.762600    -6.055507        -0.000303   
87  0.004875 -0.005213  0.044234     0.742112         0.000056   
88 -0.381420  0.555147  0.044234     1.118405        -0.000132   
89 -0.564912  0.916257  0.851068     0.646809        -0.000030   

    feature: baspred  feature: sp  
0           0.000012    -0.000004  
1           0.000106     0.000050  
2           0.000016    -0.000004  
3          -0.000070    -0.000027  
4           0.000038     0.000057  
..               ...          ...  
85          0.000049     0.000435  
86         -0.001577     0.000394  
87         -0.000287    -0.000065  
88         -0.000075     0.000118  
89         -0.000471    -0.000201  

[90 rows x 23 columns]

**model 5**

In [102]:
# load model into obj model
model = models_NN[4]


M = 10  # the number of random samples to calculate marginal contribution from
n_features = len(bins[0].columns)
feature_idxs = [7, 10, 16]
sample_to_explain = list()
shapley_value_all = list()


for df in bins:  # for each bin
    samplex = df.sample(10)  # sample 10 rows
    sample_to_explain.append(samplex)  # append them to a list
    xarray = samplex.values   # convert them to array
    
    for i in range(10):
        x = xarray[i]  # set x as the instance of interest aka the sample of index i
        print("selected instance: ", x)  # print out the instance of interest
        shapley_values = []

        for i in range(3):   # for each feature of interest
            x_idx = [7, 10, 16]
            marg_contri_feature = []

            feature_of_interest = feature_idxs[i]  # select the feature we are examining
            print("Index of feature of interest: ", feature_of_interest)
            x_idx.remove(feature_of_interest)  # the rest of the features we are about to examine

            all_combinations = []  # all coalitions of features minus the feature of interest
            for r in range(1, len(x_idx) + 1):   # generate combinations of features
                combinations_of_length_r = list(combinations(x_idx, r))
                all_combinations.extend(combinations_of_length_r)

            for coalition in all_combinations:  # for each coalition
                coalition = list(coalition)
                print('the current coalition: ', coalition)
                weight = math.factorial(len(coalition)) * math.factorial(n_features - len(coalition)-1)/ math.factorial(n_features)
                print("weight of this coalition: ", weight)

                marg_contri_coalition = []  # marginal contributions of this coalition

                for _ in range(M):
                    z = df.sample(1).values[0]  # random select sample    

                    # construct two new instances
                    x_orig = np.array([x[i] if i in coalition + [feature_of_interest] else z[i] for i in range(n_features)])
                    x_rando = np.array([x[i] if i in coalition else z[i] for i in range(n_features)])             

                    # calculate marginal contribution
                    marginal_contribution = model.predict(x_orig.reshape(1, -1))[0][0] - model.predict(x_rando.reshape(1, -1))[0][0]
                    marg_contri_coalition.append(marginal_contribution)

                sigma_j = sum(marg_contri_coalition) / len(marg_contri_coalition)
                shapley_coalition = sigma_j*weight  # for one coaltion examined for feature of interest
                marg_contri_feature.append(shapley_coalition)

            shapley_j = sum(marg_contri_feature)  # shapley value of feature j
            shapley_values.append(shapley_j)

            print("feature of interest: ", feature_of_interest)
            print("shapley value of this feature: ", shapley_j)
            print('--------')
            print('--------')
        shapley_value_all.append(shapley_values)

selected instance:  [-0.12510375 -0.46971501  0.13819008 -1.50627665  1.10348449  0.8798633
 -0.20056047  0.78350228 -0.11055272 -0.18796561 -0.3861325  -0.49193868
 -0.19322972 -0.60461379 -0.60987752  0.21413388 -0.36538244 -0.11073664
 -0.76259956 -0.11753366]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 47ms/step
feature of interest:  7
shapley value of this feature:  -0.00013453821657083884
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalit

1/1 [==============================] - 0s 37ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  10
shapley value of this feature:  9.134871400457028e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 45ms/step
feature of interest:  16
shapley value of this feature:  -2.611992085537715e-06
--------
--------
selected instance:  [ 0.65580451 -0.60860039 -0.33804712 -0.84075562  1.21410464  0.98707301
 -0.19750839  0.80541743 -0.11055671 -0.1879656  -0.65843004 -0.71251664
 -0.16780018 -0.66698288 -0.

1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  7
shapley value of this feature:  -9.157153671574698e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  10
shapley value of this feature:  -3.8985303815519604e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
w

1/1 [==============================] - 0s 40ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 43ms/step
feature of interest:  16
shapley value of this feature:  -4.1373736328548846e-06
--------
--------
selected instance:  [ 0.23243194  1.66582801 -1.09492916  0.55328153  1.7297134   5.3696177
 -0.2477979   0.96860536 -0.11053401 -0.18796561  0.62282635  0.59840487
  0.23897709  0.11111962 -0.13010526  0.36614627  0.16464228 -0.12782828
  0.04423431  0.29245392]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 33ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  7
s

1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  0.00023752385265689494
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 29ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 39ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  10
shapley value of this feature:  -5.078210375593071e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [7, 10]
weigh

...

1/1 [==============================] - 0s 36ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  16
shapley value of this feature:  1.6398920067613234e-05
--------
--------
selected instance:  [ 0.14236401  0.28887291  0.09450548  0.18926378  0.63458759  0.34657503
 -0.00232765  0.98756781 -0.11057136 -0.1879656  -0.40699238 -0.39965724
 -0.36788854  0.356485    0.0859682   0.15934579  0.79815617  0.24221981
  0.85106818  0.13142363]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 33ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [10, 16

1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  0.0017114388509735204
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 28ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 47ms/step
feature of interest:  10
shapley value of this feature:  2.8624421758958455e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight

1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  6.808786764632015e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 47ms/step
feature of interest:  10
shapley value of this feature:  -0.0013872264645862999
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
wei

1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 48ms/step
feature of interest:  16
shapley value of this feature:  0.0001431244088892351
--------
--------
selected instance:  [-1.44437065 -0.96242034 -1.44082886  0.27072286  1.45148841  0.78846183
 -0.26146689  0.35350831 -0.1102449  -0.1879656   1.17625179  1.40066621
  0.94151248  1.38011597  1.271626   -0.00652982 -0.57711475 -1.92502944
  0.04423431 -1.27176777]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  7
sh

1/1 [==============================] - 0s 31ms/step
feature of interest:  10
shapley value of this feature:  3.585282775807624e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 33ms/step
feature of interest:  16
shapley value of this feature:  -0.00017618985476288183
--------
--------
selected instance:  [-1.83269434  0.62873802 -1.20416471  0.13012342  0.56921572 -0.78557956
 -0.28214323 -1.66412699 -0.0468474  -0.18796557  2.81642357  2.63844278
  1.15935389  0.9224228   0.68480918  0.00987079 -0.44980636  0.32069216
  1.65790206 -1.51200778]
Index of feature of interest:  7
the current coalition:  [10]


In [103]:
all_sample = pd.concat([sample_to_explain[0], sample_to_explain[1]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[2]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[3]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[4]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[5]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[6]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[7]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[8]], ignore_index=True)

all_sample

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0  -0.125104 -0.469715  0.138190 -1.506277  1.103484  0.879863 -0.200560   
1   0.005508  0.135154 -0.419642 -1.088493 -0.202716 -0.503334 -0.244282   
2   0.655805 -0.608600 -0.338047 -0.840756  1.214105  0.987073 -0.197508   
3  -0.256864  0.793600 -0.192024  1.458838 -0.753031 -0.847905 -0.281962   
4   0.232432  1.665828 -1.094929  0.553282  1.729713  5.369618 -0.247798   
..       ...       ...       ...       ...       ...       ...       ...   
85  0.142364  0.288873  0.094505  0.189264  0.634588  0.346575 -0.002328   
86  0.722430  1.527436  1.898991  0.105499 -0.878742 -0.205122 -0.273833   
87  0.962232  0.740905  0.586968  0.582910  0.393165 -0.381938 -0.268010   
88 -1.444371 -0.962420 -1.440829  0.270723  1.451488  0.788462 -0.261467   
89 -1.832694  0.628738 -1.204165  0.130123  0.569216 -0.785580 -0.282143   

      dolvol       ill  zerotrade  baspread    retvol   idiovol      beta  \
0   0.783502 -0.110553  -0.187966 -0.386132 -0.491939 -0.193230 -0.604614   
1  -0.025004 -0.110380  -0.187966 -0.752922 -0.928480 -0.732823 -0.641636   
2   0.805417 -0.110557  -0.187966 -0.658430 -0.712517 -0.167800 -0.666983   
3  -1.619979 -0.049541   0.663627 -1.197176 -0.900109  0.266462 -1.142996   
4   0.968605 -0.110534  -0.187966  0.622826  0.598405  0.238977  0.111120   
..       ...       ...        ...       ...       ...       ...       ...   
85  0.987568 -0.110571  -0.187966 -0.406992 -0.399657 -0.367889  0.356485   
86 -0.287654 -0.109603  -0.187966 -0.058389 -0.346288  0.233738  0.274919   
87 -0.236472 -0.109076  -0.187966  0.169355 -0.001266 -0.248424 -0.891153   
88  0.353508 -0.110245  -0.187966  1.176252  1.400666  0.941512  1.380116   
89 -1.664127 -0.046847  -0.187966  2.816424  2.638443  1.159354  0.922423   

      betasq        ep        sp       agr     nincr  return(t-1)  
0  -0.609878  0.214134 -0.365382 -0.110737 -0.762600    -0.117534  
1  -0.628596  0.337631 -0.071118 -0.077228 -0.762600    -0.011947  
2  -0.641066  0.214134 -0.365382 -0.110737 -0.762600     0.571762  
3  -0.823029 -1.071396  2.241951  0.072594  0.851068    -0.257750  
4  -0.130105  0.366146  0.164642 -0.127828  0.044234     0.292454  
..       ...       ...       ...       ...       ...          ...  
85  0.085968  0.159346  0.798156  0.242220  0.851068     0.131424  
86  0.011216 -0.717612  2.737624  0.156028 -0.762600     0.641087  
87 -0.739111  0.306416  0.141873  0.563286 -0.762600     0.865176  
88  1.271626 -0.006530 -0.577115 -1.925029  0.044234    -1.271768  
89  0.684809  0.009871 -0.449806  0.320692  1.657902    -1.512008  

[90 rows x 20 columns]

In [104]:
shapleydf = pd.DataFrame(shapley_value_all, columns = ['feature: dolvol', 'feature: baspred', 'feature: sp'])
shapley_mtx = pd.concat([all_sample, shapleydf], axis=1)
shapleymtxes.append(shapley_mtx)

shapley_mtx

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0  -0.125104 -0.469715  0.138190 -1.506277  1.103484  0.879863 -0.200560   
1   0.005508  0.135154 -0.419642 -1.088493 -0.202716 -0.503334 -0.244282   
2   0.655805 -0.608600 -0.338047 -0.840756  1.214105  0.987073 -0.197508   
3  -0.256864  0.793600 -0.192024  1.458838 -0.753031 -0.847905 -0.281962   
4   0.232432  1.665828 -1.094929  0.553282  1.729713  5.369618 -0.247798   
..       ...       ...       ...       ...       ...       ...       ...   
85  0.142364  0.288873  0.094505  0.189264  0.634588  0.346575 -0.002328   
86  0.722430  1.527436  1.898991  0.105499 -0.878742 -0.205122 -0.273833   
87  0.962232  0.740905  0.586968  0.582910  0.393165 -0.381938 -0.268010   
88 -1.444371 -0.962420 -1.440829  0.270723  1.451488  0.788462 -0.261467   
89 -1.832694  0.628738 -1.204165  0.130123  0.569216 -0.785580 -0.282143   

      dolvol       ill  zerotrade  ...      beta    betasq        ep  \
0   0.783502 -0.110553  -0.187966  ... -0.604614 -0.609878  0.214134   
1  -0.025004 -0.110380  -0.187966  ... -0.641636 -0.628596  0.337631   
2   0.805417 -0.110557  -0.187966  ... -0.666983 -0.641066  0.214134   
3  -1.619979 -0.049541   0.663627  ... -1.142996 -0.823029 -1.071396   
4   0.968605 -0.110534  -0.187966  ...  0.111120 -0.130105  0.366146   
..       ...       ...        ...  ...       ...       ...       ...   
85  0.987568 -0.110571  -0.187966  ...  0.356485  0.085968  0.159346   
86 -0.287654 -0.109603  -0.187966  ...  0.274919  0.011216 -0.717612   
87 -0.236472 -0.109076  -0.187966  ... -0.891153 -0.739111  0.306416   
88  0.353508 -0.110245  -0.187966  ...  1.380116  1.271626 -0.006530   
89 -1.664127 -0.046847  -0.187966  ...  0.922423  0.684809  0.009871   

          sp       agr     nincr  return(t-1)  feature: dolvol  \
0  -0.365382 -0.110737 -0.762600    -0.117534        -0.000135   
1  -0.071118 -0.077228 -0.762600    -0.011947         0.000857   
2  -0.365382 -0.110737 -0.762600     0.571762         0.000084   
3   2.241951  0.072594  0.851068    -0.257750        -0.000092   
4   0.164642 -0.127828  0.044234     0.292454         0.000133   
..       ...       ...       ...          ...              ...   
85  0.798156  0.242220  0.851068     0.131424        -0.000155   
86  2.737624  0.156028 -0.762600     0.641087         0.001711   
87  0.141873  0.563286 -0.762600     0.865176         0.000068   
88 -0.577115 -1.925029  0.044234    -1.271768         0.000099   
89 -0.449806  0.320692  1.657902    -1.512008        -0.000661   

    feature: baspred  feature: sp  
0      -4.016543e-07    -0.000069  
1       9.134871e-05    -0.000003  
2      -4.738184e-05     0.000184  
3      -3.898530e-05    -0.000004  
4      -6.666577e-05    -0.000159  
..               ...          ...  
85     -1.300887e-05    -0.000109  
86      2.862442e-05     0.000449  
87     -1.387226e-03     0.000143  
88      3.585283e-05    -0.000176  
89      5.837354e-04     0.000150  

[90 rows x 23 columns]

**model 6**

In [105]:
# load model into obj model
model = models_NN[5]


M = 10  # the number of random samples to calculate marginal contribution from
n_features = len(bins[0].columns)
feature_idxs = [7, 10, 16]
sample_to_explain = list()
shapley_value_all = list()


for df in bins:  # for each bin
    samplex = df.sample(10)  # sample 10 rows
    sample_to_explain.append(samplex)  # append them to a list
    xarray = samplex.values   # convert them to array
    
    for i in range(10):
        x = xarray[i]  # set x as the instance of interest aka the sample of index i
        print("selected instance: ", x)  # print out the instance of interest
        shapley_values = []

        for i in range(3):   # for each feature of interest
            x_idx = [7, 10, 16]
            marg_contri_feature = []

            feature_of_interest = feature_idxs[i]  # select the feature we are examining
            print("Index of feature of interest: ", feature_of_interest)
            x_idx.remove(feature_of_interest)  # the rest of the features we are about to examine

            all_combinations = []  # all coalitions of features minus the feature of interest
            for r in range(1, len(x_idx) + 1):   # generate combinations of features
                combinations_of_length_r = list(combinations(x_idx, r))
                all_combinations.extend(combinations_of_length_r)

            for coalition in all_combinations:  # for each coalition
                coalition = list(coalition)
                print('the current coalition: ', coalition)
                weight = math.factorial(len(coalition)) * math.factorial(n_features - len(coalition)-1)/ math.factorial(n_features)
                print("weight of this coalition: ", weight)

                marg_contri_coalition = []  # marginal contributions of this coalition

                for _ in range(M):
                    z = df.sample(1).values[0]  # random select sample    

                    # construct two new instances
                    x_orig = np.array([x[i] if i in coalition + [feature_of_interest] else z[i] for i in range(n_features)])
                    x_rando = np.array([x[i] if i in coalition else z[i] for i in range(n_features)])             

                    # calculate marginal contribution
                    marginal_contribution = model.predict(x_orig.reshape(1, -1))[0][0] - model.predict(x_rando.reshape(1, -1))[0][0]
                    marg_contri_coalition.append(marginal_contribution)

                sigma_j = sum(marg_contri_coalition) / len(marg_contri_coalition)
                shapley_coalition = sigma_j*weight  # for one coaltion examined for feature of interest
                marg_contri_feature.append(shapley_coalition)

            shapley_j = sum(marg_contri_feature)  # shapley value of feature j
            shapley_values.append(shapley_j)

            print("feature of interest: ", feature_of_interest)
            print("shapley value of this feature: ", shapley_j)
            print('--------')
            print('--------')
        shapley_value_all.append(shapley_values)

selected instance:  [-0.34262681  0.03348389  0.11541939 -1.06341165 -0.21618994  0.00322028
 -0.25513194  0.23407626 -0.11029368 -0.1879656  -0.2769759  -0.55032421
 -0.26405847 -0.39237923 -0.49099375  0.29110876 -0.12307725  0.07927245
  0.85106818 -0.32761132]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 48ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  -8.470211597431822e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [16]
weight of this coalit

1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  10
shapley value of this feature:  3.3944134208324716e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  16
shapley value of this feature:  -1.7008422302049504e-06
--------
--------
selected instance:  [-1.0522642  -0.38246833 -0.29591171 -1.55582211  1.43283544  1.06220833
 -0.20022046  0.79279175 -0.11055395 -0.1879656  -0.46196274 -0.42984949
 -0.21709196 -0.61978375 -

1/1 [==============================] - 0s 23ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  2.7735109103309826e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 47ms/step
feature of interest:  10
shapley value of this feature:  -0.00014433620818917863
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
w

1/1 [==============================] - 0s 32ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 22ms/step
feature of interest:  16
shapley value of this feature:  3.54106018962393e-05
--------
--------
selected instance:  [ 0.60936985  2.76663262 -0.54942148  1.46570161 -0.72433002  1.9290203
 -0.26614429  0.41191824 -0.11014956 -0.18796561  1.91844975  2.01622153
  0.07851068 -0.20377202 -0.36880262  0.04347023  0.56649873 -0.21161655
  0.04423431  0.8734437 ]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 41ms/step
feature of interest:  7
shap

1/1 [==============================] - 0s 47ms/step
feature of interest:  7
shapley value of this feature:  1.2058396823704244e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 41ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 33ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 47ms/step
feature of interest:  10
shapley value of this feature:  0.00010401461785386875
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 24ms/step
the current coalition:  [7, 10]
weigh

...

1/1 [==============================] - 0s 35ms/step
feature of interest:  16
shapley value of this feature:  -0.000143998241438721
--------
--------
selected instance:  [ 0.79799597 -1.1800504   1.47573468 -0.88639102  0.19955521 -0.83088946
 -0.28126735 -1.71969857  0.03157455 -0.18796553  0.26870549  0.86546599
  0.24607079 -0.6213593  -0.61841857 -0.03596797  0.07064819  0.19657002
 -0.76259956  0.80253062]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 49ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 34ms/step
feature of interest:  7
shapley value of this feature:  0.00013333353883864584
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
w

1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  10
shapley value of this feature:  0.00025874480458074495
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 33ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 36ms/step
feature of interest:  16
shapley value of this feature:  -1.4082975249889997e-05
--------
--------
selected instance:  [ 0.03203018 -1.2942632   0.30621486 -1.899

1/1 [==============================] - 0s 31ms/step
feature of interest:  16
shapley value of this feature:  -0.00021311463703733614
--------
--------
selected instance:  [ 0.40628125  1.88154949 -3.96366198  2.4894818  -1.10500137 -0.46280804
 -0.27980891 -0.86662026 -0.10675586 -0.18796559  0.46184596  0.05311764
  1.25207394  0.4577393   0.18281414 -0.3173806   1.06039823  0.51012296
  0.85106818  0.40141987]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 34ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 36ms/step
feature of interest:  7
shapley value of this feature:  0.00016533064606942627
--------
--------
Index of feature of interest:  10
the current coalition:  [7]

1/1 [==============================] - 0s 32ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  10
shapley value of this feature:  0.00022616813277923745
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 36ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  16
shapley value of this feature:  -3.4142701902933277e-05
--------
--------
selected instance:  [-1.45484919 -0.44552455  0.12935556 -1.03310237  2.80147943  1.19213328
 -0.25732967  0.43254288 -0.11041948 -0.18796561  0.46502934  0.57233462
  1.29772444  0.11361328 -

1/1 [==============================] - 0s 31ms/step
feature of interest:  16
shapley value of this feature:  9.897823636120523e-05
--------
--------


In [106]:
all_sample = pd.concat([sample_to_explain[0], sample_to_explain[1]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[2]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[3]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[4]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[5]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[6]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[7]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[8]], ignore_index=True)

all_sample

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0  -0.342627  0.033484  0.115419 -1.063412 -0.216190  0.003220 -0.255132   
1   0.352285  1.595635 -0.682101  0.681915  1.537728  4.629042 -0.253905   
2  -1.052264 -0.382468 -0.295912 -1.555822  1.432835  1.062208 -0.200220   
3   1.184785  1.419865 -0.437116 -0.125594  1.715883  4.665173 -0.249384   
4   0.609370  2.766633 -0.549421  1.465702 -0.724330  1.929020 -0.266144   
..       ...       ...       ...       ...       ...       ...       ...   
85 -0.696462  0.006534 -1.759518 -0.303232 -0.255491 -0.255185 -0.256873   
86  0.032030 -1.294263  0.306215 -1.899721 -0.111383  1.271952 -0.204436   
87  0.406281  1.881549 -3.963662  2.489482 -1.105001 -0.462808 -0.279809   
88 -0.943337 -1.640710 -0.213157 -0.979479  0.399998  0.911722 -0.276557   
89 -1.454849 -0.445525  0.129356 -1.033102  2.801479  1.192133 -0.257330   

      dolvol       ill  zerotrade  baspread    retvol   idiovol      beta  \
0   0.234076 -0.110294  -0.187966 -0.276976 -0.550324 -0.264058 -0.392379   
1   0.725098 -0.110485  -0.187966  0.746948  0.470676  0.177129  0.273009   
2   0.792792 -0.110554  -0.187966 -0.461963 -0.429849 -0.217092 -0.619784   
3   0.828503 -0.110526  -0.187966  0.940199  0.783308  0.228838  0.184309   
4   0.411918 -0.110150  -0.187966  1.918450  2.016222  0.078511 -0.203772   
..       ...       ...        ...       ...       ...       ...       ...   
85  0.083780 -0.109652  -0.187966  0.741557  0.706951  1.363170  1.615700   
86  0.823695 -0.110538  -0.187966  0.087586  0.126621 -0.484384 -0.573379   
87 -0.866620 -0.106756  -0.187966  0.461846  0.053118  1.252074  0.457739   
88 -0.136796 -0.108297  -0.187966  2.488733  3.076181  1.527004  1.478306   
89  0.432543 -0.110419  -0.187966  0.465029  0.572335  1.297724  0.113613   

      betasq        ep        sp       agr     nincr  return(t-1)  
0  -0.490994  0.291109 -0.123077  0.079272  0.851068    -0.327611  
1   0.009501  0.366146  0.164642 -0.127828  0.044234     0.384609  
2  -0.617620  0.214134 -0.365382 -0.110737 -0.762600    -1.037424  
3  -0.068411  0.366146  0.164642 -0.127828  0.044234     1.126412  
4  -0.368803  0.043470  0.566499 -0.211617  0.044234     0.873444  
..       ...       ...       ...       ...       ...          ...  
85  1.609410 -0.230465 -0.580090  0.021106 -0.762600    -0.591653  
86 -0.593618  0.152228 -0.484833  0.036130 -0.762600     0.067951  
87  0.182814 -0.317381  1.060398  0.510123  0.851068     0.401420  
88  1.409461  0.059089 -0.448551 -7.814533 -0.762600    -0.458399  
89 -0.128042  0.119359  1.393355 -1.666992  0.044234    -1.397617  

[90 rows x 20 columns]

In [107]:
shapleydf = pd.DataFrame(shapley_value_all, columns = ['feature: dolvol', 'feature: baspred', 'feature: sp'])
shapley_mtx = pd.concat([all_sample, shapleydf], axis=1)
shapleymtxes.append(shapley_mtx)

shapley_mtx

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0  -0.342627  0.033484  0.115419 -1.063412 -0.216190  0.003220 -0.255132   
1   0.352285  1.595635 -0.682101  0.681915  1.537728  4.629042 -0.253905   
2  -1.052264 -0.382468 -0.295912 -1.555822  1.432835  1.062208 -0.200220   
3   1.184785  1.419865 -0.437116 -0.125594  1.715883  4.665173 -0.249384   
4   0.609370  2.766633 -0.549421  1.465702 -0.724330  1.929020 -0.266144   
..       ...       ...       ...       ...       ...       ...       ...   
85 -0.696462  0.006534 -1.759518 -0.303232 -0.255491 -0.255185 -0.256873   
86  0.032030 -1.294263  0.306215 -1.899721 -0.111383  1.271952 -0.204436   
87  0.406281  1.881549 -3.963662  2.489482 -1.105001 -0.462808 -0.279809   
88 -0.943337 -1.640710 -0.213157 -0.979479  0.399998  0.911722 -0.276557   
89 -1.454849 -0.445525  0.129356 -1.033102  2.801479  1.192133 -0.257330   

      dolvol       ill  zerotrade  ...      beta    betasq        ep  \
0   0.234076 -0.110294  -0.187966  ... -0.392379 -0.490994  0.291109   
1   0.725098 -0.110485  -0.187966  ...  0.273009  0.009501  0.366146   
2   0.792792 -0.110554  -0.187966  ... -0.619784 -0.617620  0.214134   
3   0.828503 -0.110526  -0.187966  ...  0.184309 -0.068411  0.366146   
4   0.411918 -0.110150  -0.187966  ... -0.203772 -0.368803  0.043470   
..       ...       ...        ...  ...       ...       ...       ...   
85  0.083780 -0.109652  -0.187966  ...  1.615700  1.609410 -0.230465   
86  0.823695 -0.110538  -0.187966  ... -0.573379 -0.593618  0.152228   
87 -0.866620 -0.106756  -0.187966  ...  0.457739  0.182814 -0.317381   
88 -0.136796 -0.108297  -0.187966  ...  1.478306  1.409461  0.059089   
89  0.432543 -0.110419  -0.187966  ...  0.113613 -0.128042  0.119359   

          sp       agr     nincr  return(t-1)  feature: dolvol  \
0  -0.123077  0.079272  0.851068    -0.327611        -0.000085   
1   0.164642 -0.127828  0.044234     0.384609         0.000045   
2  -0.365382 -0.110737 -0.762600    -1.037424        -0.000012   
3   0.164642 -0.127828  0.044234     1.126412         0.000028   
4   0.566499 -0.211617  0.044234     0.873444        -0.000113   
..       ...       ...       ...          ...              ...   
85 -0.580090  0.021106 -0.762600    -0.591653         0.000323   
86 -0.484833  0.036130 -0.762600     0.067951         0.000289   
87  1.060398  0.510123  0.851068     0.401420         0.000165   
88 -0.448551 -7.814533 -0.762600    -0.458399         0.000217   
89  1.393355 -1.666992  0.044234    -1.397617        -0.000177   

    feature: baspred  feature: sp  
0           0.000092     0.000149  
1           0.000034    -0.000002  
2           0.000461    -0.000119  
3          -0.000144     0.000035  
4           0.000019     0.000019  
..               ...          ...  
85          0.000259    -0.000014  
86         -0.000062    -0.000213  
87         -0.000165     0.000278  
88          0.000226    -0.000034  
89         -0.000681     0.000099  

[90 rows x 23 columns]

**model 7**

In [108]:
# load model into obj model
model = models_NN[6]


M = 10  # the number of random samples to calculate marginal contribution from
n_features = len(bins[0].columns)
feature_idxs = [7, 10, 16]
sample_to_explain = list()
shapley_value_all = list()


for df in bins:  # for each bin
    samplex = df.sample(10)  # sample 10 rows
    sample_to_explain.append(samplex)  # append them to a list
    xarray = samplex.values   # convert them to array
    
    for i in range(10):
        x = xarray[i]  # set x as the instance of interest aka the sample of index i
        print("selected instance: ", x)  # print out the instance of interest
        shapley_values = []

        for i in range(3):   # for each feature of interest
            x_idx = [7, 10, 16]
            marg_contri_feature = []

            feature_of_interest = feature_idxs[i]  # select the feature we are examining
            print("Index of feature of interest: ", feature_of_interest)
            x_idx.remove(feature_of_interest)  # the rest of the features we are about to examine

            all_combinations = []  # all coalitions of features minus the feature of interest
            for r in range(1, len(x_idx) + 1):   # generate combinations of features
                combinations_of_length_r = list(combinations(x_idx, r))
                all_combinations.extend(combinations_of_length_r)

            for coalition in all_combinations:  # for each coalition
                coalition = list(coalition)
                print('the current coalition: ', coalition)
                weight = math.factorial(len(coalition)) * math.factorial(n_features - len(coalition)-1)/ math.factorial(n_features)
                print("weight of this coalition: ", weight)

                marg_contri_coalition = []  # marginal contributions of this coalition

                for _ in range(M):
                    z = df.sample(1).values[0]  # random select sample    

                    # construct two new instances
                    x_orig = np.array([x[i] if i in coalition + [feature_of_interest] else z[i] for i in range(n_features)])
                    x_rando = np.array([x[i] if i in coalition else z[i] for i in range(n_features)])             

                    # calculate marginal contribution
                    marginal_contribution = model.predict(x_orig.reshape(1, -1))[0][0] - model.predict(x_rando.reshape(1, -1))[0][0]
                    marg_contri_coalition.append(marginal_contribution)

                sigma_j = sum(marg_contri_coalition) / len(marg_contri_coalition)
                shapley_coalition = sigma_j*weight  # for one coaltion examined for feature of interest
                marg_contri_feature.append(shapley_coalition)

            shapley_j = sum(marg_contri_feature)  # shapley value of feature j
            shapley_values.append(shapley_j)

            print("feature of interest: ", feature_of_interest)
            print("shapley value of this feature: ", shapley_j)
            print('--------')
            print('--------')
        shapley_value_all.append(shapley_values)

selected instance:  [ 0.47849748  0.45289831 -1.1216705  -0.11474577  0.11251983  0.29228303
 -0.21330282  0.58954065 -0.11051654 -0.1879656  -0.45995601 -0.74599426
 -0.54822913 -0.62836464 -0.62195523  0.23016463 -0.25307307  0.06229291
 -0.76259956  0.4154966 ]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 48ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 48ms/step
feature of interest:  7
shapley value of this feature:  -2.6451398928960166e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 33ms/step
the current coalition:  [16]
weight of this coali

1/1 [==============================] - 0s 20ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 47ms/step
feature of interest:  10
shapley value of this feature:  1.9391823086168685e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 40ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 33ms/step
feature of interest:  16
shapley value of this feature:  8.091260651834527e-06
--------
--------
selected instance:  [-0.72818856 -0.98330722  0.17132911 -0.72674325  5.21325538 -0.17433475
 -0.27853683 -0.37645729 -0.10808439 -0.18796559  0.21713573 -0.14762429
  1.03176824 -0.24343326 -0.

1/1 [==============================] - 0s 40ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 28ms/step
feature of interest:  7
shapley value of this feature:  0.00010283836111840274
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 48ms/step
feature of interest:  10
shapley value of this feature:  -0.00021209669879457927
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
w

1/1 [==============================] - 0s 32ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 48ms/step
feature of interest:  16
shapley value of this feature:  -3.2862062805620904e-05
--------
--------
selected instance:  [ 4.22463996  4.11568979  4.39893921  2.83218135 -0.6863724  -0.12655489
 -0.27463437 -0.90462951 -0.10782774 -0.1879656   2.47773777  2.93459768
  0.30006589 -1.96565874 -0.8922924   0.58134967  1.918343    0.26022588
  1.65790206  6.30873076]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 24ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7


1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  9.760108068367543e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 35ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  10
shapley value of this feature:  -6.052667318641793e-07
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 43ms/step
the current coalition:  [7, 10]
weight

...

1/1 [==============================] - 0s 32ms/step
feature of interest:  16
shapley value of this feature:  -0.0004131474874216562
--------
--------
selected instance:  [ 1.76013608  0.27853768  2.78602826  0.83330291 -0.47462915 -0.73021856
 -0.27685875 -1.06019848 -0.10290188 -0.18796553 -0.42559447  0.11138988
  0.33247488  0.20400285 -0.05140949  0.25821449 -0.25386253  0.23579137
 -0.76259956  1.50063795]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  7
shapley value of this feature:  5.6176957189601065e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]


1/1 [==============================] - 0s 47ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  16
shapley value of this feature:  0.00022633283758503306
--------
--------
selected instance:  [-0.03383388  0.49347475 -0.07145815  0.15292418 -0.04702169 -0.19305399
  0.29878401  1.11358358 -0.11058871 -0.1879656  -1.13400875 -1.14057662
 -1.05536194 -0.598995   -0.60698416  0.2432111  -0.30010286  0.31122059
 -0.76259956 -0.05295909]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 24ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16

1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 28ms/step
feature of interest:  7
shapley value of this feature:  0.0002787328785971591
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 34ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 37ms/step
feature of interest:  10
shapley value of this feature:  -0.0006987257713550014
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 35ms/step
the current coalition:  [10]
wei

1/1 [==============================] - 0s 31ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 25ms/step
feature of interest:  16
shapley value of this feature:  -0.0001057477896945954
--------
--------
selected instance:  [-0.13186287 -0.54166142  0.01643522 -1.38902234 -0.23433106  0.37564669
  0.10913979  1.27033221 -0.11055226 -0.1879656   0.48082866  0.52312811
 -0.75569083 -0.76024322 -0.68452688  0.20176542 -0.33342825 -1.25904572
 -0.76259956 -0.05981253]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 48ms/step
the current coalition:  [10, 16

1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  3.638030547234747e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 34ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  10
shapley value of this feature:  -2.508416477786867e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 33ms/step
the current coalition:  [7, 10]
weight

In [109]:
all_sample = pd.concat([sample_to_explain[0], sample_to_explain[1]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[2]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[3]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[4]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[5]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[6]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[7]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[8]], ignore_index=True)

all_sample

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0   0.478497  0.452898 -1.121670 -0.114746  0.112520  0.292283 -0.213303   
1  -0.315587 -0.038463 -0.103602 -1.000633 -0.056457 -0.398783 -0.246444   
2  -0.728189 -0.983307  0.171329 -0.726743  5.213255 -0.174335 -0.278537   
3   0.572502 -1.064027 -0.380535 -0.374197  4.822046  0.115103 -0.278027   
4   4.224640  4.115690  4.398939  2.832181 -0.686372 -0.126555 -0.274634   
..       ...       ...       ...       ...       ...       ...       ...   
85 -0.033834  0.493475 -0.071458  0.152924 -0.047022 -0.193054  0.298784   
86  0.739994  0.013597  0.208417  0.168452 -0.071541 -0.099789 -0.027074   
87  0.745373  0.085287  0.408009  0.097538  0.084068 -0.089339 -0.060641   
88 -0.131863 -0.541661  0.016435 -1.389022 -0.234331  0.375647  0.109140   
89  0.175401 -0.587243  0.650529 -0.155691 -0.866912 -0.411834 -0.281203   

      dolvol       ill  zerotrade  baspread    retvol   idiovol      beta  \
0   0.589541 -0.110517  -0.187966 -0.459956 -0.745994 -0.548229 -0.628365   
1   0.110733 -0.110309  -0.187966 -0.697884 -0.804385 -0.684895 -0.640847   
2  -0.376457 -0.108084  -0.187966  0.217136 -0.147624  1.031768 -0.243433   
3  -0.535471 -0.109019  -0.187966 -0.012472 -0.314519  1.047183 -0.272046   
4  -0.904630 -0.107828  -0.187966  2.477738  2.934598  0.300066 -1.965659   
..       ...       ...        ...       ...       ...       ...       ...   
85  1.113584 -0.110589  -0.187966 -1.134009 -1.140577 -1.055362 -0.598995   
86  0.850175 -0.110563  -0.187966 -0.818886 -0.806116 -0.817856 -0.060060   
87  0.723925 -0.110575  -0.187966 -0.829448 -0.914069 -0.845473 -0.185175   
88  1.270332 -0.110552  -0.187966  0.480829  0.523128 -0.755691 -0.760243   
89 -0.836141 -0.099663  -0.187966 -0.343474 -0.572133 -0.352912 -0.892983   

      betasq        ep        sp       agr     nincr  return(t-1)  
0  -0.621955  0.230165 -0.253073  0.062293 -0.762600     0.415497  
1  -0.628204  0.337631 -0.071118 -0.077228  1.657902    -0.312113  
2  -0.395790  0.556444  0.089930 -0.537117  0.044234    -0.686115  
3  -0.414832  0.545496  0.089930 -0.537117  0.044234     0.522657  
4  -0.892292  0.581350  1.918343  0.260226  1.657902     6.308731  
..       ...       ...       ...       ...       ...          ...  
85 -0.606984  0.243211 -0.300103  0.311221 -0.762600    -0.052959  
86 -0.265247  0.122369 -0.451428  0.087596 -0.762600     0.639281  
87 -0.355912  0.172421 -0.408288 -0.630228  0.851068     0.641261  
88 -0.684527  0.201765 -0.333428 -1.259046 -0.762600    -0.059813  
89 -0.739821 -0.461986 -0.393475  0.697769 -0.762600     0.153355  

[90 rows x 20 columns]

In [110]:
shapleydf = pd.DataFrame(shapley_value_all, columns = ['feature: dolvol', 'feature: baspred', 'feature: sp'])
shapley_mtx = pd.concat([all_sample, shapleydf], axis=1)
shapleymtxes.append(shapley_mtx)

shapley_mtx

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0   0.478497  0.452898 -1.121670 -0.114746  0.112520  0.292283 -0.213303   
1  -0.315587 -0.038463 -0.103602 -1.000633 -0.056457 -0.398783 -0.246444   
2  -0.728189 -0.983307  0.171329 -0.726743  5.213255 -0.174335 -0.278537   
3   0.572502 -1.064027 -0.380535 -0.374197  4.822046  0.115103 -0.278027   
4   4.224640  4.115690  4.398939  2.832181 -0.686372 -0.126555 -0.274634   
..       ...       ...       ...       ...       ...       ...       ...   
85 -0.033834  0.493475 -0.071458  0.152924 -0.047022 -0.193054  0.298784   
86  0.739994  0.013597  0.208417  0.168452 -0.071541 -0.099789 -0.027074   
87  0.745373  0.085287  0.408009  0.097538  0.084068 -0.089339 -0.060641   
88 -0.131863 -0.541661  0.016435 -1.389022 -0.234331  0.375647  0.109140   
89  0.175401 -0.587243  0.650529 -0.155691 -0.866912 -0.411834 -0.281203   

      dolvol       ill  zerotrade  ...      beta    betasq        ep  \
0   0.589541 -0.110517  -0.187966  ... -0.628365 -0.621955  0.230165   
1   0.110733 -0.110309  -0.187966  ... -0.640847 -0.628204  0.337631   
2  -0.376457 -0.108084  -0.187966  ... -0.243433 -0.395790  0.556444   
3  -0.535471 -0.109019  -0.187966  ... -0.272046 -0.414832  0.545496   
4  -0.904630 -0.107828  -0.187966  ... -1.965659 -0.892292  0.581350   
..       ...       ...        ...  ...       ...       ...       ...   
85  1.113584 -0.110589  -0.187966  ... -0.598995 -0.606984  0.243211   
86  0.850175 -0.110563  -0.187966  ... -0.060060 -0.265247  0.122369   
87  0.723925 -0.110575  -0.187966  ... -0.185175 -0.355912  0.172421   
88  1.270332 -0.110552  -0.187966  ... -0.760243 -0.684527  0.201765   
89 -0.836141 -0.099663  -0.187966  ... -0.892983 -0.739821 -0.461986   

          sp       agr     nincr  return(t-1)  feature: dolvol  \
0  -0.253073  0.062293 -0.762600     0.415497        -0.000026   
1  -0.071118 -0.077228  1.657902    -0.312113        -0.000010   
2   0.089930 -0.537117  0.044234    -0.686115        -0.000042   
3   0.089930 -0.537117  0.044234     0.522657         0.000103   
4   1.918343  0.260226  1.657902     6.308731         0.000031   
..       ...       ...       ...          ...              ...   
85 -0.300103  0.311221 -0.762600    -0.052959         0.000068   
86 -0.451428  0.087596 -0.762600     0.639281         0.000279   
87 -0.408288 -0.630228  0.851068     0.641261        -0.000170   
88 -0.333428 -1.259046 -0.762600    -0.059813        -0.001276   
89 -0.393475  0.697769 -0.762600     0.153355         0.000036   

    feature: baspred  feature: sp  
0          -0.000254     0.000031  
1           0.000019     0.000008  
2           0.000060    -0.000052  
3          -0.000212    -0.000033  
4          -0.000070    -0.000107  
..               ...          ...  
85         -0.000015    -0.000119  
86         -0.000699     0.000023  
87          0.000117    -0.000106  
88          0.000088     0.000023  
89         -0.000025    -0.000030  

[90 rows x 23 columns]

**model 8**

In [111]:
# load model into obj model
model = models_NN[7]


M = 10  # the number of random samples to calculate marginal contribution from
n_features = len(bins[0].columns)
feature_idxs = [7, 10, 16]
sample_to_explain = list()
shapley_value_all = list()


for df in bins:  # for each bin
    samplex = df.sample(10)  # sample 10 rows
    sample_to_explain.append(samplex)  # append them to a list
    xarray = samplex.values   # convert them to array
    
    for i in range(10):
        x = xarray[i]  # set x as the instance of interest aka the sample of index i
        print("selected instance: ", x)  # print out the instance of interest
        shapley_values = []

        for i in range(3):   # for each feature of interest
            x_idx = [7, 10, 16]
            marg_contri_feature = []

            feature_of_interest = feature_idxs[i]  # select the feature we are examining
            print("Index of feature of interest: ", feature_of_interest)
            x_idx.remove(feature_of_interest)  # the rest of the features we are about to examine

            all_combinations = []  # all coalitions of features minus the feature of interest
            for r in range(1, len(x_idx) + 1):   # generate combinations of features
                combinations_of_length_r = list(combinations(x_idx, r))
                all_combinations.extend(combinations_of_length_r)

            for coalition in all_combinations:  # for each coalition
                coalition = list(coalition)
                print('the current coalition: ', coalition)
                weight = math.factorial(len(coalition)) * math.factorial(n_features - len(coalition)-1)/ math.factorial(n_features)
                print("weight of this coalition: ", weight)

                marg_contri_coalition = []  # marginal contributions of this coalition

                for _ in range(M):
                    z = df.sample(1).values[0]  # random select sample    

                    # construct two new instances
                    x_orig = np.array([x[i] if i in coalition + [feature_of_interest] else z[i] for i in range(n_features)])
                    x_rando = np.array([x[i] if i in coalition else z[i] for i in range(n_features)])             

                    # calculate marginal contribution
                    marginal_contribution = model.predict(x_orig.reshape(1, -1))[0][0] - model.predict(x_rando.reshape(1, -1))[0][0]
                    marg_contri_coalition.append(marginal_contribution)

                sigma_j = sum(marg_contri_coalition) / len(marg_contri_coalition)
                shapley_coalition = sigma_j*weight  # for one coaltion examined for feature of interest
                marg_contri_feature.append(shapley_coalition)

            shapley_j = sum(marg_contri_feature)  # shapley value of feature j
            shapley_values.append(shapley_j)

            print("feature of interest: ", feature_of_interest)
            print("shapley value of this feature: ", shapley_j)
            print('--------')
            print('--------')
        shapley_value_all.append(shapley_values)

selected instance:  [-0.56003954  0.32845122 -1.52893856  0.67598169 -0.66524142 -0.84687769
 -0.28210084 -1.69144456  0.04105772  0.70417873 -0.8689826  -0.23233439
  0.24684033 -1.14727286 -0.8242146  -1.07139556  2.24195103  0.07259441
  0.85106818 -0.52335116]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  0.00038696017965935824
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalit

1/1 [==============================] - 0s 32ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  10
shapley value of this feature:  4.413886763678308e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 33ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 38ms/step
feature of interest:  16
shapley value of this feature:  8.028153567003054e-05
--------
--------
selected instance:  [ 1.67053293  1.58456006  1.30791671  1.31374877 -0.90842292  0.33795149
 -0.26928419 -0.30274806 -0.10986448 -0.1879656   0.49138112  0.17506355
  0.11422247  0.136984   -0.1

1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7
shapley value of this feature:  4.116112355426041e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 32ms/step
feature of interest:  10
shapley value of this feature:  -0.0001100740917789483
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
wei

1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  16
shapley value of this feature:  0.000128142806995464
--------
--------
selected instance:  [-0.76108671  4.18388183 -4.79153096  2.28082046  0.65593666  2.72370804
 -0.27426003  0.45555115 -0.11004628 -0.18796561  0.85907979  0.26383925
  0.99571221 -1.2722839  -0.85532781  0.58134967  1.918343    0.26022588
  1.65790206 -0.68588992]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  7
sha

1/1 [==============================] - 0s 22ms/step
feature of interest:  7
shapley value of this feature:  0.0001894990798652346
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 38ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 48ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 47ms/step
feature of interest:  10
shapley value of this feature:  4.037203806403436e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 33ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 47ms/step
the current coalition:  [7, 10]
weight 

...

1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 20ms/step
feature of interest:  10
shapley value of this feature:  0.00011530251944797079
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  16
shapley value of this feature:  7.188166224817086e-05
--------
--------
selected instance:  [ 1.48727552  1.14391262 -0.22850795 -1.30798

1/1 [==============================] - 0s 32ms/step
feature of interest:  16
shapley value of this feature:  -0.00020175857834343671
--------
--------
selected instance:  [-0.92008543  0.20867469 -0.47966158 -0.80976523  1.58988407 -0.28338241
 -0.26512307 -0.10567198 -0.11004733 -0.1879656   0.09382385  0.13649213
  0.10908993 -0.61308991 -0.6142161   0.20729437 -0.50332111  0.56407934
  0.85106818 -0.8560001 ]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 26ms/step
feature of interest:  7
shapley value of this feature:  -6.393653819914797e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]

1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 34ms/step
feature of interest:  10
shapley value of this feature:  -8.936727337800619e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 32ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 33ms/step
feature of interest:  16
shapley value of this feature:  5.215583532525777e-06
--------
--------
selected instance:  [-0.81921203 -0.03761568  0.66824805  1.54621078  6.66044044 -0.11657689
 -0.0279379   0.9015906  -0.1105551  -0.1879656  -0.16121302 -0.27204246
  0.47771991 -1.56202036 -0.

1/1 [==============================] - 0s 32ms/step
feature of interest:  16
shapley value of this feature:  -8.3635974544705e-06
--------
--------
selected instance:  [-0.16042377  0.49709419 -0.82994167  0.950192   -0.09749843 -0.79106964
 -0.2150662  -0.28792561 -0.10959605 -0.18796555 -0.50043986 -0.50103116
 -0.66273412  0.25637973 -0.00536818  0.13550676 -0.48117413 -0.54982379
  1.65790206 -0.15224321]
Index of feature of interest:  7
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 42ms/step
the current coalition:  [16]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 38ms/step
the current coalition:  [10, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 40ms/step
feature of interest:  7
shapley value of this feature:  4.249577023829633e-05
--------
--------
Index of feature of interest:  10
the current coalition:  [7]
wei

1/1 [==============================] - 0s 47ms/step
the current coalition:  [7, 16]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 47ms/step
feature of interest:  10
shapley value of this feature:  -7.159205110013832e-05
--------
--------
Index of feature of interest:  16
the current coalition:  [7]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 31ms/step
the current coalition:  [10]
weight of this coalition:  0.002631578947368421
1/1 [==============================] - 0s 40ms/step
the current coalition:  [7, 10]
weight of this coalition:  0.00029239766081871346
1/1 [==============================] - 0s 31ms/step
feature of interest:  16
shapley value of this feature:  -6.859484128654003e-05
--------
--------
selected instance:  [ 2.28899838 -1.97813539  2.19117583 -1.21143798 -1.3913486   1.50032448
 -0.28392718 -1.91124353 -0.08797585 -0.18796561  5.04343676  4.66759995
  3.89446061  0.04640883 -0

In [112]:
all_sample = pd.concat([sample_to_explain[0], sample_to_explain[1]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[2]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[3]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[4]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[5]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[6]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[7]], ignore_index=True)
all_sample = pd.concat([all_sample, sample_to_explain[8]], ignore_index=True)

all_sample

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0  -0.560040  0.328451 -1.528939  0.675982 -0.665241 -0.846878 -0.282101   
1   0.032310 -0.035879  0.288332 -1.136633 -0.033477 -0.343237 -0.252879   
2   1.670533  1.584560  1.307917  1.313749 -0.908423  0.337951 -0.269284   
3   0.569998 -0.459702  0.034972 -0.805170  0.340675  0.354796 -0.200848   
4  -0.761087  4.183882 -4.791531  2.280820  0.655937  2.723708 -0.274260   
..       ...       ...       ...       ...       ...       ...       ...   
85  0.478958  0.175892  0.466674  0.398894  0.326187  0.728967 -0.265789   
86 -0.819212 -0.037616  0.668248  1.546211  6.660440 -0.116577 -0.027938   
87 -0.160424  0.497094 -0.829942  0.950192 -0.097498 -0.791070 -0.215066   
88 -1.878165  4.296074 -2.527009  1.293682 -0.693845  0.687244 -0.234368   
89  2.288998 -1.978135  2.191176 -1.211438 -1.391349  1.500324 -0.283927   

      dolvol       ill  zerotrade  baspread    retvol   idiovol      beta  \
0  -1.691445  0.041058   0.704179 -0.868983 -0.232334  0.246840 -1.147273   
1  -0.029249 -0.109956  -0.187966 -0.529586 -0.299114 -0.365379 -0.590131   
2  -0.302748 -0.109864  -0.187966  0.491381  0.175064  0.114222  0.136984   
3   0.515715 -0.110511  -0.187966  0.060158 -0.027765 -0.155370 -0.628750   
4   0.455551 -0.110046  -0.187966  0.859080  0.263839  0.995712 -1.272284   
..       ...       ...        ...       ...       ...       ...       ...   
85  0.235375 -0.110133  -0.187966 -0.472454 -0.440050  0.092819 -0.486070   
86  0.901591 -0.110555  -0.187966 -0.161213 -0.272042  0.477720 -1.562020   
87 -0.287926 -0.109596  -0.187966 -0.500440 -0.501031 -0.662734  0.256380   
88  0.585790 -0.110439  -0.187966  0.596102  1.516489  0.928615  0.298594   
89 -1.911244 -0.087976  -0.187966  5.043437  4.667600  3.894461  0.046409   

      betasq        ep        sp       agr     nincr  return(t-1)  
0  -0.824215 -1.071396  2.241951  0.072594  0.851068    -0.523351  
1  -0.602392  0.284879 -0.065209  0.290871  0.851068     0.037209  
2  -0.108571  0.043470  0.566499 -0.211617  0.044234     1.443649  
3  -0.622149  0.444989 -0.241285 -0.275871 -0.762600     0.532629  
4  -0.855328  0.581350  1.918343  0.260226  1.657902    -0.685890  
..       ...       ...       ...       ...       ...          ...  
85 -0.545905  0.149987 -0.398503 -1.231833  0.044234     0.429523  
86 -0.901145  0.101507 -0.387614  0.353096 -0.762600    -0.783158  
87 -0.005368  0.135507 -0.481174 -0.549824  1.657902    -0.152243  
88  0.032614 -0.211275 -0.512121  0.180448  0.851068    -1.743929  
89 -0.182700 -0.782553 -0.594384  0.921180  1.657902     2.728831  

[90 rows x 20 columns]

In [113]:
shapleydf = pd.DataFrame(shapley_value_all, columns = ['feature: dolvol', 'feature: baspred', 'feature: sp'])
shapley_mtx = pd.concat([all_sample, shapleydf], axis=1)
shapleymtxes.append(shapley_mtx)

shapley_mtx

mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
0  -0.560040  0.328451 -1.528939  0.675982 -0.665241 -0.846878 -0.282101   
1   0.032310 -0.035879  0.288332 -1.136633 -0.033477 -0.343237 -0.252879   
2   1.670533  1.584560  1.307917  1.313749 -0.908423  0.337951 -0.269284   
3   0.569998 -0.459702  0.034972 -0.805170  0.340675  0.354796 -0.200848   
4  -0.761087  4.183882 -4.791531  2.280820  0.655937  2.723708 -0.274260   
..       ...       ...       ...       ...       ...       ...       ...   
85  0.478958  0.175892  0.466674  0.398894  0.326187  0.728967 -0.265789   
86 -0.819212 -0.037616  0.668248  1.546211  6.660440 -0.116577 -0.027938   
87 -0.160424  0.497094 -0.829942  0.950192 -0.097498 -0.791070 -0.215066   
88 -1.878165  4.296074 -2.527009  1.293682 -0.693845  0.687244 -0.234368   
89  2.288998 -1.978135  2.191176 -1.211438 -1.391349  1.500324 -0.283927   

      dolvol       ill  zerotrade  ...      beta    betasq        ep  \
0  -1.691445  0.041058   0.704179  ... -1.147273 -0.824215 -1.071396   
1  -0.029249 -0.109956  -0.187966  ... -0.590131 -0.602392  0.284879   
2  -0.302748 -0.109864  -0.187966  ...  0.136984 -0.108571  0.043470   
3   0.515715 -0.110511  -0.187966  ... -0.628750 -0.622149  0.444989   
4   0.455551 -0.110046  -0.187966  ... -1.272284 -0.855328  0.581350   
..       ...       ...        ...  ...       ...       ...       ...   
85  0.235375 -0.110133  -0.187966  ... -0.486070 -0.545905  0.149987   
86  0.901591 -0.110555  -0.187966  ... -1.562020 -0.901145  0.101507   
87 -0.287926 -0.109596  -0.187966  ...  0.256380 -0.005368  0.135507   
88  0.585790 -0.110439  -0.187966  ...  0.298594  0.032614 -0.211275   
89 -1.911244 -0.087976  -0.187966  ...  0.046409 -0.182700 -0.782553   

          sp       agr     nincr  return(t-1)  feature: dolvol  \
0   2.241951  0.072594  0.851068    -0.523351         0.000387   
1  -0.065209  0.290871  0.851068     0.037209        -0.000026   
2   0.566499 -0.211617  0.044234     1.443649        -0.000208   
3  -0.241285 -0.275871 -0.762600     0.532629         0.000041   
4   1.918343  0.260226  1.657902    -0.685890         0.000067   
..       ...       ...       ...          ...              ...   
85 -0.398503 -1.231833  0.044234     0.429523        -0.000061   
86 -0.387614  0.353096 -0.762600    -0.783158        -0.000376   
87 -0.481174 -0.549824  1.657902    -0.152243         0.000042   
88 -0.512121  0.180448  0.851068    -1.743929         0.000021   
89 -0.594384  0.921180  1.657902     2.728831         0.000272   

    feature: baspred  feature: sp  
0           0.000147     0.000061  
1           0.000044     0.000080  
2           0.000014     0.000138  
3          -0.000110     0.000128  
4          -0.000029    -0.000194  
..               ...          ...  
85         -0.000089     0.000005  
86         -0.000184    -0.000008  
87         -0.000103    -0.000223  
88         -0.000072    -0.000069  
89          0.003365     0.000021  

[90 rows x 23 columns]

In [116]:
pd.to_pickle(shapleymtxes, 'shapleyNN.pkl')

In [114]:
shapleymtxes

[       mom1m    mom12m     chmom    indmom    mom36m      turn     mvel1  \
 0   0.528448 -0.064917  0.224326 -1.483216 -0.168396 -0.440080 -0.250366   
 1   0.113065 -1.303000  0.943732 -0.797343  7.760554 -0.459020 -0.278573   
 2   1.100338  0.380716 -0.897756 -0.299539  0.443509  0.391001 -0.199949   
 3  -1.422809 -0.984736  0.637894 -0.580499  5.650364  1.841581 -0.275316   
 4  -0.574709 -0.112385  0.772665 -0.124691 -0.451483 -0.829323 -0.282536   
 ..       ...       ...       ...       ...       ...       ...       ...   
 85  0.092011 -0.344763 -0.478638 -1.058499 -0.615742 -0.729530 -0.278275   
 86  1.197202 -0.859239  1.953603  0.541995  0.968625 -0.572433 -0.280739   
 87  0.573389 -0.567868 -0.744525 -1.939801 -0.965188  0.589148 -0.261072   
 88  0.172675  0.017609 -0.035974  0.670903 -0.078735  0.106603 -0.099266   
 89 -2.411545  0.211624 -0.260123 -0.104763  3.804903  0.855084 -0.031272   
 
       dolvol       ill  zerotrade  ...      beta    betasq        ep  \
 